#### Load in Data

In [1]:
# Import packages

import pandas as pd
import numpy as np
import altair as alt

In [2]:
# Tools

import functools
def conjunction(*conditions):
    return functools.reduce(np.logical_and, conditions)

In [3]:
%%html
    <style>
        @import url('https://fonts.googleapis.com/css?family=Encode+Sans:400');
        @import url('https://fonts.googleapis.com/css?family=Open+Sans:400');
        @import url('https://fonts.googleapis.com/css?family=Open+Sans:700');
    </style>

In [54]:
def catalyst(*args, **kwargs):
    font = "Times New Roman"
    labelFont = "Times New Roman" 
    sourceFont = "Times New Roman"
    # Axes
    axisColor = "#000000"
    gridColor = "#DEDDDD"
    # Colors
    main_palette = [   '#2980B9', #(light blue)
        '#003366', #(dark blue)
        '#FFAE19', #(gold)
        '#D68910', #(dark gold)
        '#E67E22', #(orange)
        '#D35400', #(dark orange)
        '#FF4500', #(red)
        '#FF6162', #(dark pink/red)
        '#438B28', #(green)
        '#45B39D', #(teal)
        '#99ADC1', #(light gray)
        '#212F3C', #(dark gray)
    ]
    return {
        "width": 800, 
        "height": 400, 
        "config": {
            "title": {
                "fontSize": 18,
                "font": font,
                "anchor": "center",
                "fontColor": "#000000",
            },
            "axisX": {
                "domain": True,
                "domainColor": axisColor,
                #"domainWidth": 1,
                "grid": False,
                "labelFont": labelFont,
                "labelFontSize": 14,
                #"labelAngle": 0,
                #"tickColor": axisColor,
                #"tickSize": 5, 
                "titleFont": font,
                "titleFontSize": 14,
                "titleFontWeight": "normal",
                #"titlePadding": 10, 
                "title": "X Axis Title (units)", 
                #"titleAngle":0
            },
            "axisY": {
                "domain": True,
                "grid": False,
                "gridColor": gridColor,
                "gridWidth": 1,
                "labelFont": labelFont,
                "labelFontSize": 14,
                "labelAngle": 0,
                "ticks": False, 
                "titleFont": font,
                "titleFontSize": 14,
                "titleFontWeight": "normal",
                "titlePadding": 10, 
                "title": "Y Axis Title (units)",
                #"titleY": -10, 
                #"titleX": 18,
                #"titleAngle": 0 #-90
            },
            "range": {
                "category": main_palette
            },
            "legend": {
                "labelFont": labelFont,
                "labelFontSize": 14,
                "symbolType": "square", 
                "symbolSize": 100, 
                "titleFont": font,
                "titleFontSize": 14,
                "titleFontWeight": "normal",
                "title": "Legend", 
                "orient": "right", 
                "offset": 0, 
            },
            "tooltip":{
                "font": "Open Sans"
            },
            "view": {
                "stroke": "transparent", 
        ### MARKS CONFIGURATIONS ###
           "text": {
               "font": "Times New Roman",
               "color": main_palette,
               "fontSize": 14,
               "align": "right",
               "fontWeight": 400,
               "size": 14,
           }, 
           "bar": {
                "size": 40,
                "binSpacing": 1,
                "continuousBandSize": 30,
                "discreteBandSize": 30,
                "fill": main_palette,
                "stroke": False,
           },
            }
        }
    }

In [55]:
alt.themes.register('catalyst', catalyst)
alt.themes.enable('catalyst');

In [6]:
# Load Nigeria MTF Data: Monthly Expense Details
# Number of survey respondents: 3668

chunksize = 10

mtf_list = []
chunksize = 10
for chunk in pd.read_csv("../../data/nga_housing_expense_30days.csv", encoding='latin-1', chunksize = chunksize):
    mtf_list.append(chunk)
    
expenses_30days = pd.concat(mtf_list, axis=0)
expenses_30days = pd.DataFrame(data = expenses_30days)

In [7]:
# Load Nigeria MTF Data: Electricity-2 Details

chunksize = 10

mtf_list = []
chunksize = 10
for chunk in pd.read_csv("../../data/nigeria_grid_access_ext.csv", encoding='latin-1', chunksize = chunksize):
    mtf_list.append(chunk)
    
electricity2 = pd.concat(mtf_list, axis=0)
electricity2 = pd.DataFrame(data = electricity2)
expenses_30days['c182'] = electricity2['c182']

In [8]:
# Load Nigeria MTF Data: Grid Access

chunksize = 10

mtf_list = []
chunksize = 10
for chunk in pd.read_csv("../../data/nigeria_grid_access.csv", encoding='latin-1', chunksize = chunksize):
    mtf_list.append(chunk)
    
grid_access = pd.concat(mtf_list, axis=0)
grid_access = pd.DataFrame(data = grid_access)
expenses_30days['c2'] = grid_access['c2']

In [9]:
# Load Nigeria MTF Data: Cooking Expense Related Details

chunksize = 10

mtf_list = []
chunksize = 10
for chunk in pd.read_csv("../../data/nigeria_cooking_expense.csv", encoding='latin-1', chunksize = chunksize):
    mtf_list.append(chunk)
    
cooking_expense = pd.concat(mtf_list, axis=0)
cooking_expense = pd.DataFrame(data = cooking_expense)

In [10]:
# Load Nigeria MTF Data: Cooking Fuel/Stove Details

chunksize = 10

mtf_list = []
chunksize = 10
for chunk in pd.read_csv("../../data/nigeria_cooking.csv", encoding='latin-1', chunksize = chunksize):
    mtf_list.append(chunk)
    
cooking = pd.concat(mtf_list, axis=0)
cooking = pd.DataFrame(data = cooking)

In [11]:
#find the primary stove used by each household
primary_stove = []
for i in range(cooking.shape[0]):
    if cooking['i35'][i] == 'Yes':
        primary_stove.append(cooking['i3'][i])
    else:
        primary_stove.append('NaN')
cooking['stove'] = primary_stove

In [12]:
#find the primary stove used by each household, but use expenses files so that column lengths match
primary_stove = []
for i in range(expenses_30days.shape[0]):
    if expenses_30days['i35'][i] == 'Yes':
        primary_stove.append(expenses_30days['i3'][i])
    else:
        primary_stove.append('NaN')
expenses_30days['stove'] = primary_stove

In [13]:
#Isolate monthly expense types
rent = expenses_30days[expenses_30days['item_id']=='House Rent']
mobile_topup = expenses_30days[expenses_30days['item_id']=='Mobile phone top-up  or bills']
electricity_charge = expenses_30days[expenses_30days['item_id']=='Electricity and other fuels ']
medical_expenses = expenses_30days[expenses_30days['item_id']=='Medical/pharmacy expenses ']
transportation = expenses_30days[expenses_30days['item_id']=='Transportation costs ']
internet = expenses_30days[expenses_30days['item_id']==
                           'Internet, land phone, dish, cable, and other household communication']
water = expenses_30days[expenses_30days['item_id']=='Water supply for drinking and other uses ']
soaps = expenses_30days[expenses_30days['item_id']=='Soaps, disinfectants and cleaning supplies; cosmetics and toiletries']

In [14]:
# Load Nigeria MTF Data: Weekly Expenses Details
# Number of survey respondents: 3668

chunksize = 10

mtf_list = []
chunksize = 10
for chunk in pd.read_csv("../../data/nga_housing_consumption.csv", encoding='latin-1', chunksize = chunksize):
    mtf_list.append(chunk)
    
weekly_expenses = pd.concat(mtf_list, axis=0)
weekly_expenses = pd.DataFrame(data = weekly_expenses)
weekly_expenses['c182'] = electricity2['c182']

In [15]:
#find the primary stove used by each household, but use expenses files so that column lengths match
primary_stove = []
for i in range(weekly_expenses.shape[0]):
    if weekly_expenses['i35'][i] == 'Yes':
        primary_stove.append(weekly_expenses['i3'][i])
    else:
        primary_stove.append('NaN')
weekly_expenses['stove'] = primary_stove

In [16]:
#Isolate weekly expense types
cereals = weekly_expenses[weekly_expenses['item_id']=='Cereals & cereal products ']
pulses = weekly_expenses[weekly_expenses['item_id']=='Pulses & nuts ']
milk = weekly_expenses[weekly_expenses['item_id']=='Milk & milk products ']
vegetables = weekly_expenses[weekly_expenses['item_id']=='Vegetables ']
eggs_and_meat = weekly_expenses[(weekly_expenses['item_id']=='Egg, & poultry') |
                                (weekly_expenses['item_id']=='Meat and meat products')]
sugar_salt = weekly_expenses[weekly_expenses['item_id']=='Sugar & Salt']
beverages = weekly_expenses[weekly_expenses['item_id']=='Beverages ']
other_foods = weekly_expenses[weekly_expenses['item_id']=='Other food items ']
alcohol_tobacco = weekly_expenses[weekly_expenses['item_id']=='Alcohol, tobacco and cigarettes']

In [17]:
# Load Nigeria MTF Data: Yearly Expenses Details
# Number of survey respondents: 3668

chunksize = 10

mtf_list = []
chunksize = 10
for chunk in pd.read_csv("../../data/nga_housing_expense_year.csv", encoding='latin-1', chunksize = chunksize):
    mtf_list.append(chunk)
    
yearly_expenses = pd.concat(mtf_list, axis=0)
yearly_expenses = pd.DataFrame(data = yearly_expenses)
yearly_expenses['c182'] = electricity2['c182']

In [18]:
#find the primary stove used by each household, but use expenses files so that column lengths match
primary_stove = []
for i in range(yearly_expenses.shape[0]):
    if yearly_expenses['i35'][i] == 'Yes':
        primary_stove.append(yearly_expenses['i3'][i])
    else:
        primary_stove.append('NaN')
yearly_expenses['stove'] = primary_stove

In [19]:
# Isolate yearly expenses by item id's
school_fees = yearly_expenses[yearly_expenses['item_id']=='School fees and other educational expenses ']
clothing_expenses = yearly_expenses[yearly_expenses['item_id']=='Clothing, shoes, and accessories']

#### Monthly Expenses Charts

In [88]:
# How much do you pay for rent each month?

# Data Source
alt.data_transformers.disable_max_rows()
source = rent[rent[['l_expenditure']].notnull().all(1)]

col1 = source['l_expenditure'] #!= NaN
col2 = source['elc_aggr_tier'] != 'NaN'

source = source[conjunction(col1,col2)]
df = source[['hh_id','elc_aggr_tier','l_expenditure', 'locality']]

# Locality Filter
locality_options = [None, 0, 1]
locality_labels = ['National', 'Urban', 'Rural']

locality_dropdown=alt.binding_select(
    options= locality_options, 
    labels = locality_labels, 
    name = "Locality Breakdown  ")
locality_select=alt.selection_single(
    fields=['locality'],
    bind=locality_dropdown)

# Tier Filter
tiers = [None, 'Tier 0', 'Tier 1', 'Tier 2', 'Tier 3', 'Tier 4', 'Tier 5']
tier_labels = ['All Tiers', 'Tier 0', 'Tier 1', 'Tier 2', 'Tier 3', 'Tier 4', 'Tier 5']
tier_dropdown=alt.binding_select(options=tiers, 
                                 labels = tier_labels, 
                                 name = "Electricity Tiers  ")
tier_select=alt.selection_single(fields=['elc_aggr_tier'],
                                bind=tier_dropdown)

# Percentage of responses shown in the chart
pct_responses = round(len(pd.unique(df[df[['l_expenditure']].notnull().all(1)]['hh_id'])) /
            3668 *100, 2) #change dataframe variable name

# Draw the Chart
final = alt.Chart(df).transform_joinaggregate(
    total='count(*)'
).transform_calculate(
    pct='1 / datum.total'
).mark_bar().encode(
    alt.X("l_expenditure:Q", 
          bin=alt.Bin(extent=[1, 160000], step=10000), # Change the step to adjust bin size
          scale = alt.Scale(domain=(0,160000),clamp = True), # Change the axes limits
         axis = alt.Axis(title = "Nigerian Naira")),
    alt.Y('sum(pct):Q', axis=alt.Axis(format='%'), title = ""),
    tooltip = [alt.Tooltip('l_expenditure:N', title = "Response (Binned)"), 
               alt.Tooltip('sum(pct):Q', format = '.2%', title = "Percentage")]
).transform_bin(
    "mbin",
    field="m",
    bin=alt.Bin(maxbins=20) # Specify the maximum number of bins
).add_selection(
    locality_select
).transform_filter(
    locality_select
).add_selection(
    tier_select
).transform_filter(
    tier_select 
).properties(
    height = 400,
    width = 500,
    title={
      "text": ["How much do you pay for rent each month?"], 
 #     "subtitle": ["You are viewing {}% of responses from the Nigeria Multi-Tiered Framework Survey.".format(pct_responses), " "],
      "color": "black",
      "subtitleColor": "black", "offset":40
    }
)

final = alt.concat(final,
    title=alt.TitleParams(
        ['', '',  
         'This chart includes responses from {}% of households in the Nigeria MTF survey sample (total size = 3,668).'.format(
             pct_responses),
         'Blank charts indicate that no data matches dropdown filter selection(s).', ''],
        baseline='bottom',
        orient='bottom',
        anchor='start',
        font = 'Times New Roman',
        fontWeight='normal',
        fontStyle = "italic",
        fontSize=15)
)

final

alt.ConcatChart(...)

In [89]:
# Save as an HTML file
final.save('monthly_rent.html')

# Save as a JSON file
final.save('monthly_rent.json')

In [21]:
for i in range(cooking_expense.shape[0]):
    if cooking_expense['k6'][i] != 'Yes' and cooking_expense['k6'][i] != 'No':
        cooking_expense['k6'][i] == "Do not Know"
cooking_expense['k6'].value_counts()

No            652
Yes           319
Dont Know      4
Name: k6, dtype: int64

In [53]:
cooking_expense.columns.tolist()

['Unnamed: 0',
 'hh_id',
 'k_start',
 'k1',
 'k2',
 'index_random_3b',
 'random_number_1',
 'index_random_2b',
 'fuelwood_stove_type',
 'wood_full_price',
 'random_percentage_price_fuel',
 'k_amount_1',
 'k3',
 'k3a',
 'wood_6month',
 'k4',
 'k5',
 'k5_oth',
 'wood_12month',
 'k6',
 'k7',
 'k7_oth',
 'wood_24month',
 'k8',
 'k9',
 'k9_oth',
 'charcoal_stove_type',
 'charc_full_price',
 'charcoal_part_price',
 'k_amount_2',
 'k3_charcoal',
 'k3a_charcoal',
 'charcoal_6month',
 'k4_charcoal',
 'k5_charcoal',
 'k5_oth_charcoal',
 'charcoal_12month',
 'k6_charcoal',
 'k7_charcoal',
 'k7_oth_charcoal',
 'charcoal_24month',
 'k8_charcoal',
 'k9_charcoal',
 'k9_oth_charcoal',
 'elc_aggr_tier',
 'locality']

In [88]:
cooking_expense[['index_random_3b','index_random_2b','fuelwood_stove_type', 'wood_full_price', 'random_percentage_price_fuel', 'wood_12month', 'k_amount_1','k6']]

index_random_3b  index_random_2b  \
0                   0                0   
1                   0                1   
2                   0                0   
3                   1                0   
4                   0                0   
...               ...              ...   
3401                0                1   
3402                1                0   
3403                0                1   
3404                1                0   
3405                0                1   

                                    fuelwood_stove_type  wood_full_price  \
0            Aspirational wood ICS available in country          12000.0   
1     Popular affordable wood ICS available in local...           9000.0   
2            Aspirational wood ICS available in country          12000.0   
3            Aspirational wood ICS available in country          12000.0   
4            Aspirational wood ICS available in country          12000.0   
...                                                 ...              ...   
3401  Popular affordable wood ICS available in local...           9000.0   
3402         Aspirational wood ICS available in country          12000.0   
3403  Popular affordable wood ICS available in local...           9000.0   
3404         Aspirational wood ICS available in country          12000.0   
3405  Popular affordable wood ICS available in local...           9000.0   

      random_percentage_price_fuel  wood_12month  k_amount_1   k6  
0                           3960.0         330.0      3960.0  NaN  
1                           2970.0         247.0      2970.0  NaN  
2                           3960.0         330.0      3960.0  NaN  
3                           7920.0         660.0      7920.0   No  
4                           3960.0         330.0      3960.0  NaN  
...                            ...           ...         ...  ...  
3401                        2970.0         247.0      2970.0  NaN  
3402                        7920.0         660.0      7920.0   No  
3403                        2970.0         247.0      2970.0  NaN  
3404                        7920.0         660.0      7920.0   No  
3405                        2970.0         247.0      2970.0  Yes  

[3406 rows x 8 columns]

In [90]:
cooking_expense['index_random_3b'].isna().sum()

0

In [91]:
cooking_expense['index_random_3b'].value_counts()

1    1711
0    1695
Name: index_random_3b, dtype: int64

In [92]:
cooking_expense['index_random_2b'].isna().sum()

0

In [93]:
cooking_expense['index_random_2b'].value_counts()

1    1723
0    1683
Name: index_random_2b, dtype: int64

In [76]:
(cooking_expense['wood_full_price'] == 12000).sum() + (cooking_expense['wood_full_price'] == 9000).sum() == cooking_expense.shape[0]

False

In [77]:
(cooking_expense['wood_full_price'] == 12000).sum()

1579

In [78]:
(cooking_expense['wood_full_price'] == 9000).sum()

1590

In [85]:
cooking_expense['wood_full_price'].isna().sum()

237

In [84]:
cooking_expense[cooking_expense['wood_full_price'].isna()][['fuelwood_stove_type', 'wood_full_price', 'random_percentage_price_fuel', 'wood_12month', 'k_amount_1','k6']].head()

fuelwood_stove_type  wood_full_price  random_percentage_price_fuel  \
208                 NaN              NaN                           NaN   
209                 NaN              NaN                           NaN   
210                 NaN              NaN                           NaN   
211                 NaN              NaN                           NaN   
214                 NaN              NaN                           NaN   

     wood_12month  k_amount_1   k6  
208           NaN         NaN  NaN  
209           NaN         NaN  NaN  
210           NaN         NaN  NaN  
211           NaN         NaN  NaN  
214           NaN         NaN  NaN

In [75]:
# All households asked for WTP at 33% or 66% of ICS price?
cooking_expense[cooking_expense['wood_full_price'] == 12000]['random_percentage_price_fuel'].value_counts()

7920.0    807
3960.0    772
Name: random_percentage_price_fuel, dtype: int64

In [86]:
cooking_expense[cooking_expense['wood_full_price'] == 9000]['random_percentage_price_fuel'].value_counts()

2970.0    814
5940.0    776
Name: random_percentage_price_fuel, dtype: int64

In [73]:
cooking_expense[cooking_expense['wood_full_price'] == 12000]['random_percentage_price_fuel'].isna().sum()

0

In [70]:
cooking_expense[(cooking_expense['wood_full_price'] == 12000) & (cooking_expense['k6'] == 'Yes')][['wood_full_price', 'k6', 'random_percentage_price_fuel']]

wood_full_price   k6  random_percentage_price_fuel
22            12000.0  Yes                        7920.0
29            12000.0  Yes                        7920.0
86            12000.0  Yes                        3960.0
101           12000.0  Yes                        3960.0
103           12000.0  Yes                        7920.0
...               ...  ...                           ...
3343          12000.0  Yes                        3960.0
3358          12000.0  Yes                        3960.0
3360          12000.0  Yes                        7920.0
3362          12000.0  Yes                        7920.0
3384          12000.0  Yes                        7920.0

[161 rows x 3 columns]

In [69]:
# WTP Fuel vs Reason Why/Why not

# Data
alt.data_transformers.disable_max_rows()
source = cooking_expense[cooking_expense[['k6', 'k7']].notnull().all(1)]

col1 = source['k6'] != 'NaN'
col2 = source['elc_aggr_tier'] != 'NaN'

source = source[conjunction(col1,col2)]
df = source[['hh_id','elc_aggr_tier','k6', 'k7', 'locality']]

# Configure common options
base = alt.Chart(df).transform_aggregate(
    chart_count='count()',
    groupby=['k6', 'k7']
).encode(
    alt.X('k6:O', 
          scale=alt.Scale(paddingInner=0), 
          title = "Willingness to Pay for Cooking Fuel"),
    alt.Y('k7:O', 
          scale=alt.Scale(paddingInner=0), 
          title = "Reason Why Respondent Cannot Accept Offer"),
)

# Configure heatmap
heatmap = base.mark_rect().encode(
    color=alt.Color('chart_count:Q',
        scale=alt.Scale(scheme='blues'),
        legend=None
    )
)

# Configure text
text = base.mark_text(baseline='middle'
).transform_joinaggregate(
    count = 'count(chart_count)',
    groupby = ['k6', 'k7']
).transform_calculate(
    pct = alt.datum.chart_count / df.shape[0]
).encode(
    text=alt.Text('pct:Q', format = '.2%'),
    color=alt.condition(
        alt.datum.chart_count < 300, # Change the color of the text here
        alt.value('black'),
        alt.value('white')
    )
)

# Roof filter
#roofs = [None, 'Corrugated iron sheet', 'Concrete/Cement', 'Thatch', 'Wood and mud', 'Bamboo/Reed', 
 #        'Plastic canvas', 'Asbestos', 'Bricks']
#roof_labels = ['All roof types', 'Corrugated iron sheet', 'Concrete/Cement', 'Thatch', 'Wood and mud', 'Bamboo/Reed', 
 #        'Plastic canvas', 'Asbestos', 'Bricks']
#roof_dropdown=alt.binding_select(options=roofs, labels = roof_labels, name = "Roofs  ")
#roof_select=alt.selection_single(fields=['b_b_11'],
 #                               bind=roof_dropdown)

# Percentage of responses shown in the chart
pct_responses = round(len(pd.unique(df[df[['k6']].notnull().all(1)]['hh_id'])) /
            3668 *100, 2) #change dataframe variable name    

# Draw the chart
final = (heatmap + text).properties(
    height = 300,
    width = 800
).add_selection(
    locality_select
).transform_filter(
    locality_select
).add_selection(
    tier_select
).transform_filter(
    tier_select 
# ).add_selection(
#     roof_select
# ).transform_filter(
#     roof_select
).properties(
    title={
      "text": ["For households whose primary cooking fuel is wood (or crop residues),",
               "would you be willing to pay ${CF} for this improved cookstove,",
               "if you were given 12 months to make the payment?"], #Willingness to Pay for Cooking Fuel (between 200 and 600 nairas) within 12 Months'], 
    #  "subtitle": ["You are viewing XX% of responses from the Kenya Multi-Tiered Framework Survey.", " "],
      "color": "black",
      "subtitleColor": "black", "offset":40,
        "offset": 30
    }
)

final = alt.concat(final,
    title=alt.TitleParams(
        ['', '',  
         'This chart includes responses from {}% of households in the Nigeria MTF survey sample (total size = 3,668).'.format(
             pct_responses),
         'Blank charts indicate that no data matches dropdown filter selection(s).', ''],
        baseline='bottom',
        orient='bottom',
        anchor='start',
        font = 'Times New Roman',
        fontWeight='normal',
        fontStyle = "italic",
        fontSize=15)
)

final

alt.ConcatChart(...)

In [23]:
# Save as an HTML file
#final.save('wtp_fuelwood_stove.html')

# Save as a JSON file
#final.save('wtp_fuelwood_stove.json')

In [24]:
# How much do you pay for your primary cooking fuel each month?

# Data Source
alt.data_transformers.disable_max_rows()
source = cooking[cooking[['i36a']].notnull().all(1)] #change variable name

col1 = source['i36a'] #!= NaN, change variable
col2 = source['elc_aggr_tier'] != 'NaN'

source = source[conjunction(col1,col2)]
df = source[['hh_id','elc_aggr_tier','i36a', 'locality', 'i19a', 'stove']] #change variable name

#Fuel filter
primary_fuel = [None, 'Wood purchased', 'Wood collected', 'Charcoal', 'Kerosene', 'Crop Residue/Plant Biomass', 
        'LPG/cooking gas', 'Garbage', 'Electric', 'Piped Natural Gas', "Charcoal Briquettes", 'Coal Briquette',
               'Biomass Briquette', 'Coal/lignite', 'Other, specify']
primary_fuel_labels = ['All Fuel Types', 'Wood purchased', 'Wood collected', 'Charcoal', 'Kerosene',
                       'Crop Residue/Plant Biomass', 'LPG/cooking gas', 'Garbage', 'Electric', 'Piped Natural Gas',
                       "Charcoal Briquettes", 'Coal Briquette', 'Biomass Briquette', 'Coal/lignite','Other']
primary_fuel_dropdown=alt.binding_select(options=primary_fuel, labels = primary_fuel_labels, name = "Fuel Type  ")
primary_fuel_select=alt.selection_single(fields=['i19a'],
                               bind=primary_fuel_dropdown)

# Cookstove Filter
stove = [None, "3-Stone/Open Fire Stove", "Manufactured Stove Traditional", "Koresone Stove", "LPG/Natural Gas Stove",
        "Electric Stove"]
stove_labels = ['All Stove Types', '3-Stone/Open Fire Stove', 'Manufactured Stove Traditional', "Koresone Stove",
               "LPG/Natural Gas Stove", "Electric Stove"]
stove_dropdown=alt.binding_select(options=stove, 
                                 labels = stove_labels, 
                                 name = "Stove Type  ")
stove_select=alt.selection_single(fields=['stove'],
                                bind=stove_dropdown)

# Locality Filter
locality_options = [None, 0, 1]
locality_labels = ['National', 'Urban', 'Rural']

locality_dropdown=alt.binding_select(
    options= locality_options, 
    labels = locality_labels, 
    name = "Locality Breakdown  ")
locality_select=alt.selection_single(
    fields=['locality'],
    bind=locality_dropdown)

# Tier Filter
tiers = [None, 'Tier 0', 'Tier 1', 'Tier 2', 'Tier 3', 'Tier 4', 'Tier 5']
tier_labels = ['All Tiers', 'Tier 0', 'Tier 1', 'Tier 2', 'Tier 3', 'Tier 4', 'Tier 5']
tier_dropdown=alt.binding_select(options=tiers, 
                                 labels = tier_labels, 
                                 name = "Electricity Tiers  ")
tier_select=alt.selection_single(fields=['elc_aggr_tier'],
                                bind=tier_dropdown)

# Percentage of responses shown in the chart
pct_responses = round(len(pd.unique(df[df[['i36a']].notnull().all(1)]['hh_id'])) /
            3668 *100, 2) #change dataframe variable name

# Draw the Chart
final = alt.Chart(df).transform_joinaggregate(
    total='count(*)'
).transform_calculate(
    pct='1 / datum.total'
).mark_bar().encode(
    alt.X("i36a:Q", #change variable name
          bin=alt.Bin(extent=[1, 72000], step=5000), # Change the step to adjust bin size
          scale = alt.Scale(domain=(0,72000),clamp = True), # Change the axes limits
         axis = alt.Axis(title = "Nigerian Naira")),
    alt.Y('sum(pct):Q', axis=alt.Axis(format='%'), title = ""),
    tooltip = [alt.Tooltip('i36a:Q', title = "Response (Binned)"), 
               alt.Tooltip('sum(pct):Q', format = '.2%', title = "Percentage")]
).transform_bin(
    "mbin",
    field="m",
    bin=alt.Bin(maxbins=20) # Specify the maximum number of bins
).add_selection(
    stove_select
).transform_filter(
    stove_select
).add_selection(
    primary_fuel_select
).transform_filter(
    primary_fuel_select
).add_selection(
    locality_select
).transform_filter(
    locality_select
).add_selection(
    tier_select
).transform_filter(
    tier_select 
).properties(
    height = 400,
    width = 500,
    title={
      "text": ["How much do you spend on your primary cooking fuel each month?"], 
 #     "subtitle": ["You are viewing {}% of responses from the Nigeria Multi-Tiered Framework Survey.".format(pct_responses), " "],
      "color": "black",
      "subtitleColor": "black", "offset":40,
        "offset": 40
    }
)

final = alt.concat(final,
    title=alt.TitleParams(
        ['', '',  
         'This chart includes responses from {}% of households in the Nigeria MTF survey sample (total size = 3,668).'.format(
             pct_responses),
         'Blank charts indicate that no data matches dropdown filter selection(s).', ''],
        baseline='bottom',
        orient='bottom',
        anchor='start',
        font = 'Times New Roman',
        fontWeight='normal',
        fontStyle = "italic",
        fontSize=15)
)

final

alt.ConcatChart(...)

In [25]:
# Save as an HTML file
#final.save('primary_cooking_fuel_expense.html')

# Save as a JSON file
#final.save('primary_cooking_fuel_expense.json')

In [26]:
cooking['i6'].describe()

count       877.000000
mean       4050.006842
std       10046.924284
min          50.000000
25%         500.000000
50%        1500.000000
75%        3500.000000
max      140000.000000
Name: i6, dtype: float64

In [27]:
cooking['i6'].max()

140000.0

In [30]:
# How much did you pay for this stove?

# Data Source
alt.data_transformers.disable_max_rows()
source = cooking[cooking[['i6']].notnull().all(1)] #change variable name

col1 = source['i6'] #!= NaN, change variable
col2 = source['elc_aggr_tier'] != 'NaN'

source = source[conjunction(col1,col2)]
df = source[['hh_id','elc_aggr_tier','i6', 'locality', 'i19a', 'i19b', 'stove']] #change variable name

# Percentage of responses shown in the chart
pct_responses = round(len(pd.unique(df[df[['i6']].notnull().all(1)]['hh_id'])) /
            3668 *100, 2) #change dataframe variable name

# Primary fuel filter
primary_fuel = [None, 'Wood purchased', 'Wood collected', 'Charcoal', 'Kerosene', 'Crop Residue/Plant Biomass', 
        'LPG/cooking gas', 'Garbage', 'Electric', 'Piped Natural Gas', "Charcoal Briquettes", 'Coal Briquette',
               'Biomass Briquette', 'Coal/lignite', 'Other, specify']
primary_fuel_labels = ['All Fuel Types', 'Wood purchased', 'Wood collected', 'Charcoal', 'Kerosene',
                       'Crop Residue/Plant Biomass', 'LPG/cooking gas', 'Garbage', 'Electric', 'Piped Natural Gas',
                       "Charcoal Briquettes", 'Coal Briquette', 'Biomass Briquette', 'Coal/lignite','Other']
primary_fuel_dropdown=alt.binding_select(options=primary_fuel, labels = primary_fuel_labels, name = "Primary Fuel Type  ")
primary_fuel_select=alt.selection_single(fields=['i19a'],
                               bind=primary_fuel_dropdown)

# Secondary fuel filter
second_fuel = [None, 'Wood purchased', 'Wood collected', 'Charcoal', 'Kerosene', 'Crop Residue/Plant Biomass', 
        'LPG/cooking gas', 'Garbage', 'Electric', 'Piped Natural Gas', "Charcoal Briquettes", 'Coal Briquette',
               'Biomass Briquette', 'Coal/lignite', 'Other, specify']
second_fuel_labels = ['All Fuel Types', 'Wood purchased', 'Wood collected', 'Charcoal', 'Kerosene',
                       'Crop Residue/Plant Biomass', 'LPG/cooking gas', 'Garbage', 'Electric', 'Piped Natural Gas',
                       "Charcoal Briquettes", 'Coal Briquette', 'Biomass Briquette', 'Coal/lignite','Other']
second_fuel_dropdown=alt.binding_select(options=second_fuel, labels = second_fuel_labels, name = "Secondary Fuel Type  ")
second_fuel_select=alt.selection_single(fields=['i19b'],
                               bind=second_fuel_dropdown)

# Cookstove Filter
stove = [None, "3-Stone/Open Fire Stove", "Manufactured Stove Traditional", "Koresone Stove", "LPG/Natural Gas Stove",
        "Electric Stove"]
stove_labels = ['All Stove Types', '3-Stone/Open Fire Stove', 'Manufactured Stove Traditional', "Koresone Stove",
               "LPG/Natural Gas Stove", "Electric Stove"]
stove_dropdown=alt.binding_select(options=stove, 
                                 labels = stove_labels, 
                                 name = "Stove Type  ")
stove_select=alt.selection_single(fields=['stove'],
                                bind=stove_dropdown)

# Locality Filter
locality_options = [None, 0, 1]
locality_labels = ['National', 'Urban', 'Rural']

locality_dropdown=alt.binding_select(
    options= locality_options, 
    labels = locality_labels, 
    name = "Locality Breakdown  ")
locality_select=alt.selection_single(
    fields=['locality'],
    bind=locality_dropdown)

# Tier Filter
tiers = [None, 'Tier 0', 'Tier 1', 'Tier 2', 'Tier 3', 'Tier 4', 'Tier 5']
tier_labels = ['All Tiers', 'Tier 0', 'Tier 1', 'Tier 2', 'Tier 3', 'Tier 4', 'Tier 5']
tier_dropdown=alt.binding_select(options=tiers, 
                                 labels = tier_labels, 
                                 name = "Electricity Tiers  ")
tier_select=alt.selection_single(fields=['elc_aggr_tier'],
                                bind=tier_dropdown)


# Draw the Chart
final = alt.Chart(df).transform_joinaggregate(
    total='count(*)'
).transform_calculate(
    pct='1 / datum.total'
).mark_bar().encode(
    alt.X("i6:Q", #change variable name
          bin=alt.Bin(extent=[50, 65000], step=2500), # Change the step to adjust bin size
          scale = alt.Scale(domain=(0,65000),clamp = True), # Change the axes limits
         axis = alt.Axis(title = "Nigerian Naira")),
    alt.Y('sum(pct):Q', axis=alt.Axis(format='%'), title = ""),
    tooltip = [alt.Tooltip('i6:Q', title = "Response (Binned)"), 
               alt.Tooltip('sum(pct):Q', format = '.2%', title = "Percentage")]
).transform_bin(
    "mbin",
    field="m",
    bin=alt.Bin(maxbins=20) # Specify the maximum number of bins
).add_selection(
    second_fuel_select
).transform_filter(
    second_fuel_select
).add_selection(
    primary_fuel_select
).transform_filter(
    primary_fuel_select
).add_selection(
    stove_select
).transform_filter(
    stove_select
).add_selection(
    locality_select
).transform_filter(
    locality_select
).add_selection(
    tier_select
).transform_filter(
    tier_select 
).properties(
    height = 400,
    width = 500,
    title={
      "text": ["How much did you pay for your primary cooking stove?"], 
 #     "subtitle": ["You are viewing {}% of responses from the Nigeria Multi-Tiered Framework Survey.".format(pct_responses), " "],
      "color": "black",
      "subtitleColor": "black", "offset":40,
        "offset": 20
    }
)

final = alt.concat(final,
    title=alt.TitleParams(
        ['', '',  
         'This chart includes responses from {}% of households in the Nigeria MTF survey sample (total size = 3,668).'.format(
             pct_responses),
         'Blank charts indicate that no data matches dropdown filter selection(s).', ''],
        baseline='bottom',
        orient='bottom',
        anchor='start',
        font = 'Times New Roman',
        fontWeight='normal',
        fontStyle = "italic",
        fontSize=15)
)

final

alt.ConcatChart(...)

In [31]:
# Save as an HTML file
#final.save('primary_cooking_stove_cost.html')

# Save as a JSON file
#final.save('primary_cooking_stove_cost.json')

In [80]:
# How much do you spend on mobile top up each month?

# Data Source
alt.data_transformers.disable_max_rows()
source = mobile_topup[mobile_topup[['l_expenditure']].notnull().all(1)]

col1 = source['l_expenditure'] #!= NaN
col2 = source['elc_aggr_tier'] != 'NaN'

source = source[conjunction(col1,col2)]
df = source[['hh_id','elc_aggr_tier','l_expenditure', 'locality', 'i19a', 'stove']]


# Percentage of responses shown in the chart
pct_responses = round(len(pd.unique(df[df[['l_expenditure']].notnull().all(1)]['hh_id'])) /
            3668 *100, 2) #change dataframe variable name

# Draw the Chart
final = alt.Chart(df).transform_joinaggregate(
    total='count(*)'
).transform_calculate(
    pct='1 / datum.total'
).mark_bar().encode(
    alt.X("l_expenditure:Q", 
          bin=alt.Bin(extent=[1, 60000], step=5000), # Change the step to adjust bin size
          scale = alt.Scale(domain=(0,60000),clamp = True), # Change the axes limits
         axis = alt.Axis(title = "Nigerian Naira")),
    alt.Y('sum(pct):Q', axis=alt.Axis(format='%'), title = ""),
    tooltip = [alt.Tooltip('l_expenditure:N', title = "Response (Binned)"), 
               alt.Tooltip('sum(pct):Q', format = '.2%', title = "Percentage")]
).transform_bin(
    "mbin",
    field="m",
    bin=alt.Bin(maxbins=20) # Specify the maximum number of bins
).add_selection(
    locality_select
).transform_filter(
    locality_select
).add_selection(
    tier_select
).transform_filter(
    tier_select 
).properties(
    height = 400,
    width = 500,
    title={
      "text": ["Amount Spent on Mobile Phone Top-up Per Month"], 
 #     "subtitle": ["You are viewing {}% of responses from the Nigeria Multi-Tiered Framework Survey.".format(pct_responses), " "],
      "color": "black",
      "subtitleColor": "black", "offset":40
    }
)

final = alt.concat(final, padding = {"left": 20, "right": 0, "bottom": 0, "top": 0},
    title=alt.TitleParams(
        ['', '',  
         'This chart includes responses from {}% of households in the Nigeria MTF survey sample (total size = 3,668).'.format(
             pct_responses),
         'Blank charts indicate that no data matches dropdown filter selection(s).', ''],
        baseline='bottom',
        orient='bottom',
        anchor='start',
        font = 'Times New Roman',
        fontWeight='normal',
        fontStyle = "italic",
        fontSize=15)
)

final

alt.ConcatChart(...)

In [81]:
# Save as an HTML file
final.save('mobile_phone_top_up_monthly_expense.html')

# Save as a JSON file
final.save('mobile_phone_top_up_monthly_expense.json')

In [78]:
# How much do you spend on electricity each month?

# Data Source
alt.data_transformers.disable_max_rows()
source = electricity_charge[electricity_charge[['l_expenditure']].notnull().all(1)]

col1 = source['l_expenditure'] #!= NaN
col2 = source['elc_aggr_tier'] != 'NaN'

source = source[conjunction(col1,col2)]
df = source[['hh_id','elc_aggr_tier','l_expenditure', 'locality', 'stove', 'c182', 'c2']]


# Percentage of responses shown in the chart
pct_responses = round(len(pd.unique(df[df[['l_expenditure']].notnull().all(1)]['hh_id'])) /
            3668 *100, 2) #change dataframe variable name


#Fuel filter
primary_fuel = [None, 'Wood purchased', 'Wood collected', 'Charcoal', 'Kerosene', 'Crop Residue/Plant Biomass', 
        'LPG/cooking gas', 'Garbage', 'Electric', 'Piped Natural Gas', "Charcoal Briquettes", 'Coal Briquette',
               'Biomass Briquette', 'Coal/lignite', 'Other, specify']
primary_fuel_labels = ['All Fuel Types', 'Wood purchased', 'Wood collected', 'Charcoal', 'Kerosene',
                       'Crop Residue/Plant Biomass', 'LPG/cooking gas', 'Garbage', 'Electric', 'Piped Natural Gas',
                       "Charcoal Briquettes", 'Coal Briquette', 'Biomass Briquette', 'Coal/lignite','Other']
primary_fuel_dropdown=alt.binding_select(options=primary_fuel, labels = primary_fuel_labels, name = "Fuel Type  ")
primary_fuel_select=alt.selection_single(fields=['i19a'],
                               bind=primary_fuel_dropdown)

# Cookstove Filter
stove = [None, "3-Stone/Open Fire Stove", "Manufactured Stove Traditional", "Koresone Stove", "LPG/Natural Gas Stove",
        "Electric Stove"]
stove_labels = ['All Stove Types', '3-Stone/Open Fire Stove', 'Manufactured Stove Traditional', "Koresone Stove",
               "LPG/Natural Gas Stove", "Electric Stove"]
stove_dropdown=alt.binding_select(options=stove, 
                                 labels = stove_labels, 
                                 name = "Stove Type  ")
stove_select=alt.selection_single(fields=['stove'],
                                bind=stove_dropdown)

# Locality Filter
locality_options = [None, 0, 1]
locality_labels = ['National', 'Urban', 'Rural']

locality_dropdown=alt.binding_select(
    options= locality_options, 
    labels = locality_labels, 
    name = "Locality Breakdown  ")
locality_select=alt.selection_single(
    fields=['locality'],
    bind=locality_dropdown)

# Tier Filter
tiers = [None, 'Tier 0', 'Tier 1', 'Tier 2', 'Tier 3', 'Tier 4', 'Tier 5']
tier_labels = ['All Tiers', 'Tier 0', 'Tier 1', 'Tier 2', 'Tier 3', 'Tier 4', 'Tier 5']
tier_dropdown=alt.binding_select(options=tiers, 
                                 labels = tier_labels, 
                                 name = "Electricity Tiers  ")
tier_select=alt.selection_single(fields=['elc_aggr_tier'],
                                bind=tier_dropdown)

# Primary Source of Electricity
elec_source = [None, 'Dry-cell battery', 'National Grid Connection', 'No electricity', 'Electric generator',
              'Other, specify', 'Solar Multi-Light Product', 'Solar Home System', 'Solar Lantern',
               'Local Mini Grid connection', 'Rechargeable Battery']
elec_source_labels = ['All Responses', 'Dry-cell battery', 'National Grid Connection', 'No electricity',
                     'Electric generator', 'Other', 'Solar Multi-Light Product', 'Solar Home System', 'Solar Lantern',
                     'Local Mini Grid Connection', 'Rechargeable Battery']
elec_source_dropdown=alt.binding_select(options=elec_source, 
                                 labels = elec_source_labels, 
                                 name = "Primary source of electricity  ")
elec_source_select=alt.selection_single(fields=['c182'],
                                bind=elec_source_dropdown)


# National Grid Connection Filter
connection = [None, 'Yes', 'No']
connection_labels = ['All Responses', 'Yes', 'No']
connection_dropdown=alt.binding_select(options=connection, 
                                 labels = connection_labels, 
                                 name = "Is the household connected to the national grid?  ")
connection_select=alt.selection_single(fields=['c2'],
                                bind=connection_dropdown)

# Draw the Chart
final = alt.Chart(df).transform_joinaggregate(
    total='count(*)'
).transform_calculate(
    pct='1 / datum.total'
).mark_bar().encode(
    alt.X("l_expenditure:Q", 
          bin=alt.Bin(extent=[0, 148000], step=10000), # Change the step to adjust bin size
          scale = alt.Scale(domain=(0,148000),clamp = True), # Change the axes limits
         axis = alt.Axis(title = "Nigerian Naira")),
    alt.Y('sum(pct):Q', axis=alt.Axis(format='%'), title = ""),
    tooltip = [alt.Tooltip('l_expenditure:N', title = "Response (Binned)"), 
               alt.Tooltip('sum(pct):Q', format = '.2%', title = "Percentage")]
).transform_bin(
    "mbin",
    field="m",
    bin=alt.Bin(maxbins=20) # Specify the maximum number of bins
).add_selection(
    stove_select
).transform_filter(
    stove_select
).add_selection(
    primary_fuel_select
).transform_filter(
    primary_fuel_select
).add_selection(
    elec_source_select
).transform_filter(
    elec_source_select
).add_selection(
    connection_select
).transform_filter(
    connection_select
).add_selection(
    tier_select
).transform_filter(
    tier_select 
).add_selection(
    locality_select
).transform_filter(
    locality_select
).properties(
    height = 400,
    width = 500,
    title={
      "text": ["How much do you think you would need to spend on electricity each month?"], 
 #     "subtitle": ["You are viewing {}% of responses from the Nigeria Multi-Tiered Framework Survey.".format(pct_responses), " "],
      "color": "black",
      "subtitleColor": "black", "offset":40
    }
)

final = alt.concat(final, padding = {"left": 20, "right": 0, "bottom": 0, "top": 0},
    title=alt.TitleParams(
        ['', '',  
         'This chart includes responses from {}% of households in the Nigeria MTF survey sample (total size = 3,668).'.format(
             pct_responses),
         'Blank charts indicate that no data matches dropdown filter selection(s).', ''],
        baseline='bottom',
        orient='bottom',
        anchor='start',
        font = 'Times New Roman',
        fontWeight='normal',
        fontStyle = "italic",
        fontSize=15)
)

final

alt.ConcatChart(...)

In [79]:
# Save as an HTML file
final.save('expected_monthly_electricity_charge.html')

# Save as a JSON file
final.save('expected_monthly_electricity_charge.json')

In [84]:
# How much do you spend on medical/pharmacy expenditures each month?

# Data Source
alt.data_transformers.disable_max_rows()
source = medical_expenses[medical_expenses[['l_expenditure']].notnull().all(1)]

col1 = source['l_expenditure'] #!= NaN
col2 = source['elc_aggr_tier'] != 'NaN'

source = source[conjunction(col1,col2)]
df = source[['hh_id','elc_aggr_tier','l_expenditure', 'locality', 'c182', 'i19a', 'stove']]

# Primary Source of Electricity
elec_source = [None, 'Dry-cell battery', 'National Grid Connection', 'No electricity', 'Electric generator',
              'Other, specify', 'Solar Multi-Light Product', 'Solar Home System', 'Solar Lantern',
               'Local Mini Grid connection', 'Rechargeable Battery']
elec_source_labels = ['All Responses', 'Dry-cell battery', 'National Grid Connection', 'No electricity',
                     'Electric generator', 'Other', 'Solar Multi-Light Product', 'Solar Home System', 'Solar Lantern',
                     'Local Mini Grid Connection', 'Rechargeable Battery']
elec_source_dropdown=alt.binding_select(options=elec_source, 
                                 labels = elec_source_labels, 
                                 name = "Primary source of electricity  ")
elec_source_select=alt.selection_single(fields=['c182'],
                                bind=elec_source_dropdown)

#Edit cookstove and fuel dropdown labels
primary_fuel_dropdown=alt.binding_select(options=primary_fuel, labels = primary_fuel_labels, name =
                                         "Primary source of cooking fuel  ")
primary_fuel_select=alt.selection_single(fields=['i19a'],
                               bind=primary_fuel_dropdown)

stove_dropdown=alt.binding_select(options=stove, 
                                 labels = stove_labels, 
                                 name = "Primary cookstove type  ")
stove_select=alt.selection_single(fields=['stove'],
                                bind=stove_dropdown)

# Percentage of responses shown in the chart
pct_responses = round(len(pd.unique(df[df[['l_expenditure']].notnull().all(1)]['hh_id'])) /
            3668 *100, 2) #change dataframe variable name

# Draw the Chart
final = alt.Chart(df).transform_joinaggregate(
    total='count(*)'
).transform_calculate(
    pct='1 / datum.total'
).mark_bar().encode(
    alt.X("l_expenditure:Q", 
          bin=alt.Bin(extent=[10, 70000], step=5000), # Change the step to adjust bin size
          scale = alt.Scale(domain=(10,70000),clamp = True), # Change the axes limits
         axis = alt.Axis(title = "Nigerian Naira")),
    alt.Y('sum(pct):Q', axis=alt.Axis(format='%'), title = ""),
    tooltip = [alt.Tooltip('l_expenditure:N', title = "Response (Binned)"), 
               alt.Tooltip('sum(pct):Q', format = '.2%', title = "Percentage")],
).transform_bin(
    "mbin",
    field="m",
    bin=alt.Bin(maxbins=20) # Specify the maximum number of bins
).add_selection(
    stove_select
).transform_filter(
    stove_select
).add_selection(
    primary_fuel_select
).transform_filter(
    primary_fuel_select
).add_selection(
    elec_source_select
).transform_filter(
    elec_source_select 
).add_selection(
    locality_select
).transform_filter(
    locality_select
).properties(
    height = 400,
    width = 500,
    title={
      "text": ["Expenditures on Medical/Pharmacy Expenses per Month"], 
 #     "subtitle": ["You are viewing {}% of responses from the Nigeria Multi-Tiered Framework Survey.".format(pct_responses), " "],
      "color": "black",
      "subtitleColor": "black", 
        "offset":40
    }
)

# Adds padding so y-axis labels aren't cutoff. Example: primary source cooking fuel set to 'Garbage'
final = alt.concat(final, padding = {"left": 20, "right": 0, "bottom": 0, "top": 0},
    title=alt.TitleParams(
        ['', '',  
         'This chart includes responses from {}% of households in the Nigeria MTF survey sample (total size = 3,668).'.format(
             pct_responses),
         'Blank charts indicate that no data matches dropdown filter selection(s).', '',
         ''],
        baseline='bottom',
        orient='bottom',
        anchor='start',
        font = 'Times New Roman',
        fontWeight='normal',
        fontStyle = "italic",
        fontSize=15)
)

# Adds padding so y-axis labels aren't cutoff. Example: primary source cooking fuel set to 'Garbage'
# alt.renderers.set_embed_options(
#     padding={"left": 20, "right": 0, "bottom": 0, "top": 0}
# )

final

alt.ConcatChart(...)

In [85]:
# Save as an HTML file
final.save('monthly_medical_expenditures.html')

# Save as a JSON file
final.save('monthly_medical_expenditures.json')

In [92]:
# How much do you spend on transportation each month?

# Data Source
alt.data_transformers.disable_max_rows()
source = transportation[transportation[['l_expenditure']].notnull().all(1)]

col1 = source['l_expenditure'] #!= NaN
col2 = source['elc_aggr_tier'] != 'NaN'

source = source[conjunction(col1,col2)]
df = source[['hh_id','elc_aggr_tier','l_expenditure', 'locality', 'c182', 'i19a', 'stove']]

# Percentage of responses shown in the chart
pct_responses = round(len(pd.unique(df[df[['l_expenditure']].notnull().all(1)]['hh_id'])) /
            3668 *100, 2) #change dataframe variable name

# Draw the Chart
final = alt.Chart(df).transform_joinaggregate(
    total='count(*)'
).transform_calculate(
    pct='1 / datum.total'
).mark_bar().encode(
    alt.X("l_expenditure:Q", 
          bin=alt.Bin(extent=[100, 500000], step=20000), # Change the step to adjust bin size
          scale = alt.Scale(domain=(100,500000),clamp = True), # Change the axes limits
         axis = alt.Axis(title = "Nigerian Naira")),
    alt.Y('sum(pct):Q', axis=alt.Axis(format='%'), title = ""),
    tooltip = [alt.Tooltip('l_expenditure:N', title = "Response (Binned)"), 
               alt.Tooltip('sum(pct):Q', format = '.2%', title = "Percentage")]
).transform_bin(
    "mbin",
    field="m",
    bin=alt.Bin(maxbins=20) # Specify the maximum number of bins
).add_selection(
    stove_select
).transform_filter(
    stove_select
).add_selection(
    primary_fuel_select
).transform_filter(
    primary_fuel_select
).add_selection(
    elec_source_select
).transform_filter(
    elec_source_select 
).add_selection(
    locality_select
).transform_filter(
    locality_select
).properties(
    height = 400,
    width = 500,
    title={
      "text": ["Transportation Expenditures per Month"], 
 #     "subtitle": ["You are viewing {}% of responses from the Nigeria Multi-Tiered Framework Survey.".format(pct_responses), " "],
      "color": "black",
      "subtitleColor": "black", "offset":40
    }
)

final = alt.concat(final, padding = {"left": 20, "right": 0, "bottom": 0, "top": 0},
    title=alt.TitleParams(
        ['', '',  
         'This chart includes responses from {}% of households in the Nigeria MTF survey sample (total size = 3,668).'.format(
             pct_responses),
         'Blank charts indicate that no data matches dropdown filter selection(s).', ''],
        baseline='bottom',
        orient='bottom',
        anchor='start',
        font = 'Times New Roman',
        fontWeight='normal',
        fontStyle = "italic",
        fontSize=15)
)

final

alt.ConcatChart(...)

In [93]:
# Save as an HTML file
final.save('monthly_transportation_expenditures.html')

# Save as a JSON file
final.save('monthly_transportation_expenditures.json')

In [86]:
# How much do you spend on household communication and internet each month?

# Data Source
alt.data_transformers.disable_max_rows()
source = internet[internet[['l_expenditure']].notnull().all(1)]

col1 = source['l_expenditure'] #!= NaN
col2 = source['elc_aggr_tier'] != 'NaN'

source = source[conjunction(col1,col2)]
df = source[['hh_id','elc_aggr_tier','l_expenditure', 'locality', 'c182', 'i19a', 'stove']]

# Percentage of responses shown in the chart
pct_responses = round(len(pd.unique(df[df[['l_expenditure']].notnull().all(1)]['hh_id'])) /
            3668 *100, 2) #change dataframe variable name

# Draw the Chart
final = alt.Chart(df).transform_joinaggregate(
    total='count(*)'
).transform_calculate(
    pct='1 / datum.total'
).mark_bar().encode(
    alt.X("l_expenditure:Q", 
          bin=alt.Bin(extent=[150, 15000], step=1000), # Change the step to adjust bin size
          scale = alt.Scale(domain=(150,15000),clamp = True), # Change the axes limits
         axis = alt.Axis(title = "Nigerian Naira")),
    alt.Y('sum(pct):Q', axis=alt.Axis(format='%'), title = ""),
    tooltip = [alt.Tooltip('l_expenditure:N', title = "Response (Binned)"), 
               alt.Tooltip('sum(pct):Q', format = '.2%', title = "Percentage")]
).transform_bin(
    "mbin",
    field="m",
    bin=alt.Bin(maxbins=20) # Specify the maximum number of bins
).add_selection(
    stove_select
).transform_filter(
    stove_select
).add_selection(
    primary_fuel_select
).transform_filter(
    primary_fuel_select
).add_selection(
    elec_source_select
).transform_filter(
    elec_source_select 
).add_selection(
    locality_select
).transform_filter(
    locality_select
).properties(
    height = 400,
    width = 500,
    title={
      "text": ["Internet and Household Communication Expenditures per Month"], 
 #     "subtitle": ["You are viewing {}% of responses from the Nigeria Multi-Tiered Framework Survey.".format(pct_responses), " "],
      "color": "black",
      "subtitleColor": "black", "offset":40
    }
)

final = alt.concat(final, padding = {"left": 20, "right": 0, "bottom": 0, "top": 0},
    title=alt.TitleParams(
        ['', '',  
         'This chart includes responses from {}% of households in the Nigeria MTF survey sample (total size = 3,668).'.format(
             pct_responses),
         'Blank charts indicate that no data matches dropdown filter selection(s).', ''],
        baseline='bottom',
        orient='bottom',
        anchor='start',
        font = 'Times New Roman',
        fontWeight='normal',
        fontStyle = "italic",
        fontSize=15)
)

final

alt.ConcatChart(...)

In [87]:
# Save as an HTML file
final.save('monthly_internet_expenditures.html')

# Save as a JSON file
final.save('monthly_internet_expenditures.json')

In [168]:
# How much do you spend on household cleaning supplies each month?

# Data Source
alt.data_transformers.disable_max_rows()
source = soaps[soaps[['l_expenditure']].notnull().all(1)]

col1 = source['l_expenditure'] #!= NaN
col2 = source['elc_aggr_tier'] != 'NaN'

source = source[conjunction(col1,col2)]
df = source[['hh_id','elc_aggr_tier','l_expenditure', 'locality', 'c182', 'i19a', 'stove']]

# Percentage of responses shown in the chart
pct_responses = round(len(pd.unique(df[df[['l_expenditure']].notnull().all(1)]['hh_id'])) /
            3668 *100, 2) #change dataframe variable name

# Draw the Chart
final = alt.Chart(df).transform_joinaggregate(
    total='count(*)'
).transform_calculate(
    pct='1 / datum.total'
).mark_bar().encode(
    alt.X("l_expenditure:Q", 
          bin=alt.Bin(extent=[40, 60000], step=5000), # Change the step to adjust bin size
          scale = alt.Scale(domain=(40,60000),clamp = True), # Change the axes limits
         axis = alt.Axis(title = "Nigerian Naira")),
    alt.Y('sum(pct):Q', axis=alt.Axis(format='%'), title = ""),
    tooltip = [alt.Tooltip('l_expenditure:N', title = "Response (Binned)"), 
               alt.Tooltip('sum(pct):Q', format = '.2%', title = "Percentage")]
).transform_bin(
    "mbin",
    field="m",
    bin=alt.Bin(maxbins=20) # Specify the maximum number of bins
).add_selection(
    stove_select
).transform_filter(
    stove_select
).add_selection(
    primary_fuel_select
).transform_filter(
    primary_fuel_select
).add_selection(
    elec_source_select
).transform_filter(
    elec_source_select 
).add_selection(
    locality_select
).transform_filter(
    locality_select
).properties(
    height = 400,
    width = 500,
    title={
      "text": ["Household Cleaning Supplies and Toiletries Expenditures per Month"], 
 #     "subtitle": ["You are viewing {}% of responses from the Nigeria Multi-Tiered Framework Survey.".format(pct_responses), " "],
      "color": "black",
      "subtitleColor": "black", "offset":40
    }
)

final = alt.concat(final,
    title=alt.TitleParams(
        ['', '',  
         'This chart includes responses from {}% of households in the Nigeria MTF survey sample (total size = 3,668).'.format(
             pct_responses),
         'Blank charts indicate that no data matches dropdown filter selection(s).', ''],
        baseline='bottom',
        orient='bottom',
        anchor='start',
        font = 'Times New Roman',
        fontWeight='normal',
        fontStyle = "italic",
        fontSize=15)
)

final

alt.ConcatChart(...)

In [169]:
# Save as an HTML file
final.save('final.html')

# Save as a JSON file
final.save('final.json')

In [170]:
# How much do you spend on water supply each month?

# Data Source
alt.data_transformers.disable_max_rows()
source = water[water[['l_expenditure']].notnull().all(1)]

col1 = source['l_expenditure'] #!= NaN
col2 = source['elc_aggr_tier'] != 'NaN'

source = source[conjunction(col1,col2)]
df = source[['hh_id','elc_aggr_tier','l_expenditure', 'locality', 'c182', 'i19a', 'stove']]

# Percentage of responses shown in the chart
pct_responses = round(len(pd.unique(df[df[['l_expenditure']].notnull().all(1)]['hh_id'])) /
            3668 *100, 2) #change dataframe variable name

# Draw the Chart
final = alt.Chart(df).transform_joinaggregate(
    total='count(*)'
).transform_calculate(
    pct='1 / datum.total'
).mark_bar().encode(
    alt.X("l_expenditure:Q", 
          bin=alt.Bin(extent=[0, 60000], step=5000), # Change the step to adjust bin size
          scale = alt.Scale(domain=(0,60000),clamp = True), # Change the axes limits
         axis = alt.Axis(title = "Nigerian Naira")),
    alt.Y('sum(pct):Q', axis=alt.Axis(format='%'), title = ""),
    tooltip = [alt.Tooltip('l_expenditure:N', title = "Response (Binned)"), 
               alt.Tooltip('sum(pct):Q', format = '.2%', title = "Percentage")]
).transform_bin(
    "mbin",
    field="m",
    bin=alt.Bin(maxbins=20) # Specify the maximum number of bins
).add_selection(
    stove_select
).transform_filter(
    stove_select
).add_selection(
    primary_fuel_select
).transform_filter(
    primary_fuel_select
).add_selection(
    elec_source_select
).transform_filter(
    elec_source_select 
).add_selection(
    locality_select
).transform_filter(
    locality_select
).properties(
    height = 400,
    width = 500,
    title={
      "text": ["Water Supply Expenditures per Month"], 
 #     "subtitle": ["You are viewing {}% of responses from the Nigeria Multi-Tiered Framework Survey.".format(pct_responses), " "],
      "color": "black",
      "subtitleColor": "black", "offset":40
    }
)

final = alt.concat(final,
    title=alt.TitleParams(
        ['', '',  
         'This chart includes responses from {}% of households in the Nigeria MTF survey sample (total size = 3,668).'.format(
             pct_responses),
         'Blank charts indicate that no data matches dropdown filter selection(s).', ''],
        baseline='bottom',
        orient='bottom',
        anchor='start',
        font = 'Times New Roman',
        fontWeight='normal',
        fontStyle = "italic",
        fontSize=15)
)

final

alt.ConcatChart(...)

In [171]:
# Save as an HTML file
final.save('final.html')

# Save as a JSON file
final.save('final.json')

#### Yearly Expenses Charts

In [172]:
# How much do you spend on school fees each year?

# Data Source
alt.data_transformers.disable_max_rows()
source = school_fees[school_fees[['l_expenditure_12months']].notnull().all(1)] #change variable

col1 = source['l_expenditure_12months'] #!= NaN #change variable
col2 = source['elc_aggr_tier'] != 'NaN'

source = source[conjunction(col1,col2)]
df = source[['hh_id','elc_aggr_tier','l_expenditure_12months', 'locality', 'c182', 'i19a', 'stove']] #change variable

# Percentage of responses shown in the chart
pct_responses = round(len(pd.unique(df[df[['l_expenditure_12months']].notnull().all(1)]['hh_id'])) /
            3668 *100, 2) #change dataframe variable name

# Draw the Chart
final = alt.Chart(df).transform_joinaggregate(
    total='count(*)'
).transform_calculate(
    pct='1 / datum.total'
).mark_bar().encode(
    alt.X("l_expenditure_12months:Q", #change variable
          bin=alt.Bin(extent=[0, 1600000], step=50000), # Change the step to adjust bin size
          scale = alt.Scale(domain=(0,1600000),clamp = True), # Change the axes limits
         axis = alt.Axis(title = "Nigerian Naira")),
    alt.Y('sum(pct):Q', axis=alt.Axis(format='%'), title = ""),
    tooltip = [alt.Tooltip('l_expenditure_12months:N', title = "Response (Binned)"),  #change variable
               alt.Tooltip('sum(pct):Q', format = '.2%', title = "Percentage")]
).transform_bin(
    "mbin",
    field="m",
    bin=alt.Bin(maxbins=20) # Specify the maximum number of bins
).add_selection(
    stove_select
).transform_filter(
    stove_select
).add_selection(
    primary_fuel_select
).transform_filter(
    primary_fuel_select
).add_selection(
    elec_source_select
).transform_filter(
    elec_source_select 
).add_selection(
    locality_select
).transform_filter(
    locality_select
).properties(
    height = 400,
    width = 500,
    title={
      "text": ["School Fees and Education Expenditures per Month"], 
 #     "subtitle": ["You are viewing {}% of responses from the Nigeria Multi-Tiered Framework Survey.".format(pct_responses), " "],
      "color": "black",
      "subtitleColor": "black", "offset":40
    }
)

final = alt.concat(final,
    title=alt.TitleParams(
        ['', '',  
         'This chart includes responses from {}% of households in the Nigeria MTF survey sample (total size = 3,668).'.format(
             pct_responses),
         'Blank charts indicate that no data matches dropdown filter selection(s).', ''],
        baseline='bottom',
        orient='bottom',
        anchor='start',
        font = 'Times New Roman',
        fontWeight='normal',
        fontStyle = "italic",
        fontSize=15)
)

final

alt.ConcatChart(...)

In [173]:
# Save as an HTML file
final.save('final.html')

# Save as a JSON file
final.save('final.json')

In [174]:
# How much do you spend on clothing each year?

# Data Source
alt.data_transformers.disable_max_rows()
source = clothing_expenses[clothing_expenses[['l_expenditure_12months']].notnull().all(1)] #change variable

col1 = source['l_expenditure_12months'] #!= NaN #change variable
col2 = source['elc_aggr_tier'] != 'NaN'

source = source[conjunction(col1,col2)]
df = source[['hh_id','elc_aggr_tier','l_expenditure_12months', 'locality', 'c182', 'i19a','stove']] #change variable

# Percentage of responses shown in the chart
pct_responses = round(len(pd.unique(df[df[['l_expenditure_12months']].notnull().all(1)]['hh_id'])) /
            3668 *100, 2) #change dataframe variable name

# Draw the Chart
final = alt.Chart(df).transform_joinaggregate(
    total='count(*)'
).transform_calculate(
    pct='1 / datum.total'
).mark_bar().encode(
    alt.X("l_expenditure_12months:Q", #change variable
          bin=alt.Bin(extent=[0, 360000], step=20000), # Change the step to adjust bin size
          scale = alt.Scale(domain=(0,360000),clamp = True), # Change the axes limits
         axis = alt.Axis(title = "Nigerian Naira")),
    alt.Y('sum(pct):Q', axis=alt.Axis(format='%'), title = ""),
    tooltip = [alt.Tooltip('l_expenditure_12months:N', title = "Response (Binned)"),  #change variable
               alt.Tooltip('sum(pct):Q', format = '.2%', title = "Percentage")]
).transform_bin(
    "mbin",
    field="m",
    bin=alt.Bin(maxbins=20) # Specify the maximum number of bins
).add_selection(
    stove_select
).transform_filter(
    stove_select
).add_selection(
    primary_fuel_select
).transform_filter(
    primary_fuel_select
).add_selection(
    elec_source_select
).transform_filter(
    elec_source_select 
).add_selection(
    locality_select
).transform_filter(
    locality_select
).properties(
    height = 400,
    width = 500,
    title={
      "text": ["Clothing, Shoes, and Accessories Expenditures per Month"], 
 #     "subtitle": ["You are viewing {}% of responses from the Nigeria Multi-Tiered Framework Survey.".format(pct_responses), " "],
      "color": "black",
      "subtitleColor": "black", "offset":40
    }
)

final = alt.concat(final,
    title=alt.TitleParams(
        ['', '',  
         'This chart includes responses from {}% of households in the Nigeria MTF survey sample (total size = 3,668).'.format(
             pct_responses),
         'Blank charts indicate that no data matches dropdown filter selection(s).', ''],
        baseline='bottom',
        orient='bottom',
        anchor='start',
        font = 'Times New Roman',
        fontWeight='normal',
        fontStyle = "italic",
        fontSize=15)
)

final

alt.ConcatChart(...)

In [175]:
# Save as an HTML file
final.save('final.html')

# Save as a JSON file
final.save('final.json')

#### Weekly Expenses Charts

In [244]:
# How much do you spend on cereals each week?

# Data Source
alt.data_transformers.disable_max_rows()
source = cereals[cereals[['l_consumption_purchased']].notnull().all(1)] #change variable

col1 = source['l_consumption_purchased'] #!= NaN #change variable
col2 = source['cs_aggr_tier'] != 'NaN'

source = source[conjunction(col1,col2)]
df = source[['hh_id','cs_aggr_tier','l_consumption_purchased', 'locality', 'c182', 'i19a','stove']] #change variable

# Tier Filter
cooking_tiers = [None, 'Tier 0', 'Tier 1', 'Tier 2', 'Tier 3', 'Tier 4', 'Tier 5']
cooking_tier_labels = ['All Tiers', 'Tier 0', 'Tier 1', 'Tier 2', 'Tier 3', 'Tier 4', 'Tier 5']
cooking_tier_dropdown=alt.binding_select(options=cooking_tiers, 
                                 labels = cooking_tier_labels, 
                                 name = "Cooking Tier  ")
cooking_tier_select=alt.selection_single(fields=['cs_aggr_tier'],
                                bind=cooking_tier_dropdown)

# Percentage of responses shown in the chart
pct_responses = round(len(pd.unique(df[df[['l_consumption_purchased']].notnull().all(1)]['hh_id'])) /
            3668 *100, 2) #change dataframe variable name

# Draw the Chart
final = alt.Chart(df).transform_joinaggregate(
    total='count(*)'
).transform_calculate(
    pct='1 / datum.total'
).mark_bar().encode(
    alt.X("l_consumption_purchased:Q", #change variable
          bin=alt.Bin(extent=[0, 240000], step=10000), # Change the step to adjust bin size
          scale = alt.Scale(domain=(0,240000),clamp = True), # Change the axes limits
         axis = alt.Axis(title = "Nigerian Naira")),
    alt.Y('sum(pct):Q', axis=alt.Axis(format='%'), title = ""),
    tooltip = [alt.Tooltip('l_consumption_purchased:N', title = "Response (Binned)"),  #change variable
               alt.Tooltip('sum(pct):Q', format = '.2%', title = "Percentage")]
).transform_bin(
    "mbin",
    field="m",
    bin=alt.Bin(maxbins=20) # Specify the maximum number of bins
).add_selection(
    stove_select
).transform_filter(
    stove_select
).add_selection(
    primary_fuel_select
).transform_filter(
    primary_fuel_select
).add_selection(
    elec_source_select
).transform_filter(
    elec_source_select 
).add_selection(
    locality_select
).transform_filter(
    locality_select
).add_selection(
    cooking_tier_select
).transform_filter(
    cooking_tier_select 
).properties(
    height = 400,
    width = 500,
    title={
      "text": ["Cereals Expenditures per Week"], 
 #     "subtitle": ["You are viewing {}% of responses from the Nigeria Multi-Tiered Framework Survey.".format(pct_responses), " "],
      "color": "black",
      "subtitleColor": "black", "offset":40
    }
)

final = alt.concat(final,
    title=alt.TitleParams(
        ['', '',  
         'This chart includes responses from {}% of households in the Nigeria MTF survey sample (total size = 3,668).'.format(
             pct_responses),
         'Blank charts indicate that no data matches dropdown filter selection(s).', ''],
        baseline='bottom',
        orient='bottom',
        anchor='start',
        font = 'Times New Roman',
        fontWeight='normal',
        fontStyle = "italic",
        fontSize=15)
)

final

alt.ConcatChart(...)

In [245]:
# Save as an HTML file
final.save('final.html')

# Save as a JSON file
final.save('final.json')

In [246]:
# How much do you spend on pulses and nuts each week?

# Data Source
alt.data_transformers.disable_max_rows()
source = pulses[pulses[['l_consumption_purchased']].notnull().all(1)] #change variable

col1 = source['l_consumption_purchased'] #!= NaN #change variable
col2 = source['cs_aggr_tier'] != 'NaN'

source = source[conjunction(col1,col2)]
df = source[['hh_id','cs_aggr_tier','l_consumption_purchased', 'locality', 'c182', 'i19a','stove']] #change variable

# Percentage of responses shown in the chart
pct_responses = round(len(pd.unique(df[df[['l_consumption_purchased']].notnull().all(1)]['hh_id'])) /
            3668 *100, 2) #change dataframe variable name

# Draw the Chart
final = alt.Chart(df).transform_joinaggregate(
    total='count(*)'
).transform_calculate(
    pct='1 / datum.total'
).mark_bar().encode(
    alt.X("l_consumption_purchased:Q", #change variable
          bin=alt.Bin(extent=[0, 40000], step=2000), # Change the step to adjust bin size
          scale = alt.Scale(domain=(0,40000),clamp = True), # Change the axes limits
         axis = alt.Axis(title = "Nigerian Naira")),
    alt.Y('sum(pct):Q', axis=alt.Axis(format='%'), title = ""),
    tooltip = [alt.Tooltip('l_consumption_purchased:N', title = "Response (Binned)"),  #change variable
               alt.Tooltip('sum(pct):Q', format = '.2%', title = "Percentage")]
).transform_bin(
    "mbin",
    field="m",
    bin=alt.Bin(maxbins=20) # Specify the maximum number of bins
).add_selection(
    stove_select
).transform_filter(
    stove_select
).add_selection(
    primary_fuel_select
).transform_filter(
    primary_fuel_select
).add_selection(
    elec_source_select
).transform_filter(
    elec_source_select 
).add_selection(
    locality_select
).transform_filter(
    locality_select
).add_selection(
    cooking_tier_select
).transform_filter(
    cooking_tier_select 
).properties(
    height = 400,
    width = 500,
    title={
      "text": ["Pulses and Nuts Expenditures per Week"], 
 #     "subtitle": ["You are viewing {}% of responses from the Nigeria Multi-Tiered Framework Survey.".format(pct_responses), " "],
      "color": "black",
      "subtitleColor": "black", "offset":40
    }
)

final = alt.concat(final,
    title=alt.TitleParams(
        ['', '',  
         'This chart includes responses from {}% of households in the Nigeria MTF survey sample (total size = 3,668).'.format(
             pct_responses),
         'Blank charts indicate that no data matches dropdown filter selection(s).', ''],
        baseline='bottom',
        orient='bottom',
        anchor='start',
        font = 'Times New Roman',
        fontWeight='normal',
        fontStyle = "italic",
        fontSize=15)
)

final

alt.ConcatChart(...)

In [247]:
# Save as an HTML file
final.save('final.html')

# Save as a JSON file
final.save('final.json')

In [248]:
# How much do you spend on milk each week?

# Data Source
alt.data_transformers.disable_max_rows()
source = milk[milk[['l_consumption_purchased']].notnull().all(1)] #change variable

col1 = source['l_consumption_purchased'] #!= NaN #change variable
col2 = source['cs_aggr_tier'] != 'NaN'

source = source[conjunction(col1,col2)]
df = source[['hh_id','cs_aggr_tier','l_consumption_purchased', 'locality', 'c182', 'i19a','stove']] #change variable

# Percentage of responses shown in the chart
pct_responses = round(len(pd.unique(df[df[['l_consumption_purchased']].notnull().all(1)]['hh_id'])) /
            3668 *100, 2) #change dataframe variable name

# Draw the Chart
final = alt.Chart(df).transform_joinaggregate(
    total='count(*)'
).transform_calculate(
    pct='1 / datum.total'
).mark_bar().encode(
    alt.X("l_consumption_purchased:Q", #change variable
          bin=alt.Bin(extent=[0, 12000], step=1000), # Change the step to adjust bin size
          scale = alt.Scale(domain=(0,12000),clamp = True), # Change the axes limits
         axis = alt.Axis(title = "Nigerian Naira")),
    alt.Y('sum(pct):Q', axis=alt.Axis(format='%'), title = ""),
    tooltip = [alt.Tooltip('l_consumption_purchased:N', title = "Response (Binned)"),  #change variable
               alt.Tooltip('sum(pct):Q', format = '.2%', title = "Percentage")]
).transform_bin(
    "mbin",
    field="m",
    bin=alt.Bin(maxbins=20) # Specify the maximum number of bins
).add_selection(
    stove_select
).transform_filter(
    stove_select
).add_selection(
    primary_fuel_select
).transform_filter(
    primary_fuel_select
).add_selection(
    elec_source_select
).transform_filter(
    elec_source_select 
).add_selection(
    locality_select
).transform_filter(
    locality_select
).add_selection(
    cooking_tier_select
).transform_filter(
    cooking_tier_select 
).properties(
    height = 400,
    width = 500,
    title={
      "text": ["Milk & Milk Product Expenditures per Week"], 
 #     "subtitle": ["You are viewing {}% of responses from the Nigeria Multi-Tiered Framework Survey.".format(pct_responses), " "],
      "color": "black",
      "subtitleColor": "black", "offset":40
    }
)

final = alt.concat(final,
    title=alt.TitleParams(
        ['', '',  
         'This chart includes responses from {}% of households in the Nigeria MTF survey sample (total size = 3,668).'.format(
             pct_responses),
         'Blank charts indicate that no data matches dropdown filter selection(s).', ''],
        baseline='bottom',
        orient='bottom',
        anchor='start',
        font = 'Times New Roman',
        fontWeight='normal',
        fontStyle = "italic",
        fontSize=15)
)

final

alt.ConcatChart(...)

In [249]:
# Save as an HTML file
final.save('final.html')

# Save as a JSON file
final.save('final.json')

In [250]:
# How much do you spend on vegetables each week?

# Data Source
alt.data_transformers.disable_max_rows()
source = vegetables[vegetables[['l_consumption_purchased']].notnull().all(1)] #change variable

col1 = source['l_consumption_purchased'] #!= NaN #change variable
col2 = source['cs_aggr_tier'] != 'NaN'

source = source[conjunction(col1,col2)]
df = source[['hh_id','cs_aggr_tier','l_consumption_purchased', 'locality', 'c182', 'i19a','stove']] #change variable

# Percentage of responses shown in the chart
pct_responses = round(len(pd.unique(df[df[['l_consumption_purchased']].notnull().all(1)]['hh_id'])) /
            3668 *100, 2) #change dataframe variable name

# Draw the Chart
final = alt.Chart(df).transform_joinaggregate(
    total='count(*)'
).transform_calculate(
    pct='1 / datum.total'
).mark_bar().encode(
    alt.X("l_consumption_purchased:Q", #change variable
          bin=alt.Bin(extent=[0, 22000], step=2000), # Change the step to adjust bin size
          scale = alt.Scale(domain=(0,22000),clamp = True), # Change the axes limits
         axis = alt.Axis(title = "Nigerian Naira")),
    alt.Y('sum(pct):Q', axis=alt.Axis(format='%'), title = ""),
    tooltip = [alt.Tooltip('l_consumption_purchased:N', title = "Response (Binned)"),  #change variable
               alt.Tooltip('sum(pct):Q', format = '.2%', title = "Percentage")]
).transform_bin(
    "mbin",
    field="m",
    bin=alt.Bin(maxbins=20) # Specify the maximum number of bins
).add_selection(
    stove_select
).transform_filter(
    stove_select
).add_selection(
    primary_fuel_select
).transform_filter(
    primary_fuel_select
).add_selection(
    elec_source_select
).transform_filter(
    elec_source_select 
).add_selection(
    locality_select
).transform_filter(
    locality_select
).add_selection(
    cooking_tier_select
).transform_filter(
    cooking_tier_select 
).properties(
    height = 400,
    width = 500,
    title={
      "text": ["Vegetables Expenditures per Week"], 
 #     "subtitle": ["You are viewing {}% of responses from the Nigeria Multi-Tiered Framework Survey.".format(pct_responses), " "],
      "color": "black",
      "subtitleColor": "black", "offset":40
    }
)

final = alt.concat(final,
    title=alt.TitleParams(
        ['', '',  
         'This chart includes responses from {}% of households in the Nigeria MTF survey sample (total size = 3,668).'.format(
             pct_responses),
         'Blank charts indicate that no data matches dropdown filter selection(s).', ''],
        baseline='bottom',
        orient='bottom',
        anchor='start',
        font = 'Times New Roman',
        fontWeight='normal',
        fontStyle = "italic",
        fontSize=15)
)

final

alt.ConcatChart(...)

In [251]:
# Save as an HTML file
final.save('final.html')

# Save as a JSON file
final.save('final.json')

In [252]:
# How much do you spend on eggs/meat each week?

# Data Source
alt.data_transformers.disable_max_rows()
source = eggs_and_meat[eggs_and_meat[['l_consumption_purchased']].notnull().all(1)] #change variable

col1 = source['l_consumption_purchased'] #!= NaN #change variable
col2 = source['cs_aggr_tier'] != 'NaN'

source = source[conjunction(col1,col2)]
df = source[['hh_id','cs_aggr_tier','l_consumption_purchased', 'locality', 'c182', 'i19a','stove']] #change variable

# Percentage of responses shown in the chart
pct_responses = round(len(pd.unique(df[df[['l_consumption_purchased']].notnull().all(1)]['hh_id'])) /
            3668 *100, 2) #change dataframe variable name

# Draw the Chart
final = alt.Chart(df).transform_joinaggregate(
    total='count(*)'
).transform_calculate(
    pct='1 / datum.total'
).mark_bar().encode(
    alt.X("l_consumption_purchased:Q", #change variable
          bin=alt.Bin(extent=[0, 17000], step=1000), # Change the step to adjust bin size
          scale = alt.Scale(domain=(0,17000),clamp = True), # Change the axes limits
         axis = alt.Axis(title = "Nigerian Naira")),
    alt.Y('sum(pct):Q', axis=alt.Axis(format='%'), title = ""),
    tooltip = [alt.Tooltip('l_consumption_purchased:N', title = "Response (Binned)"),  #change variable
               alt.Tooltip('sum(pct):Q', format = '.2%', title = "Percentage")]
).transform_bin(
    "mbin",
    field="m",
    bin=alt.Bin(maxbins=20) # Specify the maximum number of bins
).add_selection(
    stove_select
).transform_filter(
    stove_select
).add_selection(
    primary_fuel_select
).transform_filter(
    primary_fuel_select
).add_selection(
    elec_source_select
).transform_filter(
    elec_source_select 
).add_selection(
    locality_select
).transform_filter(
    locality_select
).add_selection(
    cooking_tier_select
).transform_filter(
    cooking_tier_select 
).properties(
    height = 400,
    width = 500,
    title={
      "text": ["Egg, Poultry, Meat & Meat Products Expenditures per Week"], 
 #     "subtitle": ["You are viewing {}% of responses from the Nigeria Multi-Tiered Framework Survey.".format(pct_responses), " "],
      "color": "black",
      "subtitleColor": "black", "offset":40
    }
)

final = alt.concat(final,
    title=alt.TitleParams(
        ['', '',  
         'This chart includes responses from {}% of households in the Nigeria MTF survey sample (total size = 3,668).'.format(
             pct_responses),
         'Blank charts indicate that no data matches dropdown filter selection(s).', ''],
        baseline='bottom',
        orient='bottom',
        anchor='start',
        font = 'Times New Roman',
        fontWeight='normal',
        fontStyle = "italic",
        fontSize=15)
)

final

alt.ConcatChart(...)

In [253]:
# Save as an HTML file
final.save('final.html')

# Save as a JSON file
final.save('final.json')

In [254]:
# How much do you spend on sugar/salt each week?

# Data Source
alt.data_transformers.disable_max_rows()
source = sugar_salt[sugar_salt[['l_consumption_purchased']].notnull().all(1)] #change variable

col1 = source['l_consumption_purchased'] #!= NaN #change variable
col2 = source['cs_aggr_tier'] != 'NaN'

source = source[conjunction(col1,col2)]
df = source[['hh_id','cs_aggr_tier','l_consumption_purchased', 'locality', 'c182', 'i19a','stove']] #change variable

# Percentage of responses shown in the chart
pct_responses = round(len(pd.unique(df[df[['l_consumption_purchased']].notnull().all(1)]['hh_id'])) /
            3668 *100, 2) #change dataframe variable name

# Draw the Chart
final = alt.Chart(df).transform_joinaggregate(
    total='count(*)'
).transform_calculate(
    pct='1 / datum.total'
).mark_bar().encode(
    alt.X("l_consumption_purchased:Q", #change variable
          bin=alt.Bin(extent=[0, 22000], step=2000), # Change the step to adjust bin size
          scale = alt.Scale(domain=(0,22000),clamp = True), # Change the axes limits
         axis = alt.Axis(title = "Nigerian Naira")),
    alt.Y('sum(pct):Q', axis=alt.Axis(format='%'), title = ""),
    tooltip = [alt.Tooltip('l_consumption_purchased:N', title = "Response (Binned)"),  #change variable
               alt.Tooltip('sum(pct):Q', format = '.2%', title = "Percentage")]
).transform_bin(
    "mbin",
    field="m",
    bin=alt.Bin(maxbins=20) # Specify the maximum number of bins
).add_selection(
    stove_select
).transform_filter(
    stove_select
).add_selection(
    primary_fuel_select
).transform_filter(
    primary_fuel_select
).add_selection(
    elec_source_select
).transform_filter(
    elec_source_select 
).add_selection(
    locality_select
).transform_filter(
    locality_select
).add_selection(
    cooking_tier_select
).transform_filter(
    cooking_tier_select 
).properties(
    height = 400,
    width = 500,
    title={
      "text": ["Sugar & Salt Expenditures per Week"], 
 #     "subtitle": ["You are viewing {}% of responses from the Nigeria Multi-Tiered Framework Survey.".format(pct_responses), " "],
      "color": "black",
      "subtitleColor": "black", "offset":40
    }
)

final = alt.concat(final,
    title=alt.TitleParams(
        ['', '',  
         'This chart includes responses from {}% of households in the Nigeria MTF survey sample (total size = 3,668).'.format(
             pct_responses),
         'Blank charts indicate that no data matches dropdown filter selection(s).', ''],
        baseline='bottom',
        orient='bottom',
        anchor='start',
        font = 'Times New Roman',
        fontWeight='normal',
        fontStyle = "italic",
        fontSize=15)
)

final

alt.ConcatChart(...)

In [255]:
# Save as an HTML file
final.save('final.html')

# Save as a JSON file
final.save('final.json')

In [256]:
# How much do you spend on other food items each week?

# Data Source
alt.data_transformers.disable_max_rows()
source = other_foods[other_foods[['l_consumption_purchased']].notnull().all(1)] #change variable

col1 = source['l_consumption_purchased'] #!= NaN #change variable
col2 = source['cs_aggr_tier'] != 'NaN'

source = source[conjunction(col1,col2)]
df = source[['hh_id','cs_aggr_tier','l_consumption_purchased', 'locality', 'c182', 'i19a','stove']] #change variable

# Percentage of responses shown in the chart
pct_responses = round(len(pd.unique(df[df[['l_consumption_purchased']].notnull().all(1)]['hh_id'])) /
            3668 *100, 2) #change dataframe variable name

# Draw the Chart
final = alt.Chart(df).transform_joinaggregate(
    total='count(*)'
).transform_calculate(
    pct='1 / datum.total'
).mark_bar().encode(
    alt.X("l_consumption_purchased:Q", #change variable
          bin=alt.Bin(extent=[0, 13000], step=1000), # Change the step to adjust bin size
          scale = alt.Scale(domain=(0,13000),clamp = True), # Change the axes limits
         axis = alt.Axis(title = "Nigerian Naira")),
    alt.Y('sum(pct):Q', axis=alt.Axis(format='%'), title = ""),
    tooltip = [alt.Tooltip('l_consumption_purchased:N', title = "Response (Binned)"),  #change variable
               alt.Tooltip('sum(pct):Q', format = '.2%', title = "Percentage")]
).transform_bin(
    "mbin",
    field="m",
    bin=alt.Bin(maxbins=20) # Specify the maximum number of bins
).add_selection(
    stove_select
).transform_filter(
    stove_select
).add_selection(
    primary_fuel_select
).transform_filter(
    primary_fuel_select
).add_selection(
    elec_source_select
).transform_filter(
    elec_source_select 
).add_selection(
    locality_select
).transform_filter(
    locality_select
).add_selection(
    cooking_tier_select
).transform_filter(
    cooking_tier_select 
).properties(
    height = 400,
    width = 500,
    title={
      "text": ["Other Food Expenditures per Week"], 
 #     "subtitle": ["You are viewing {}% of responses from the Nigeria Multi-Tiered Framework Survey.".format(pct_responses), " "],
      "color": "black",
      "subtitleColor": "black", "offset":40
    }
)

final = alt.concat(final,
    title=alt.TitleParams(
        ['', '',  
         'This chart includes responses from {}% of households in the Nigeria MTF survey sample (total size = 3,668).'.format(
             pct_responses),
         'Blank charts indicate that no data matches dropdown filter selection(s).', ''],
        baseline='bottom',
        orient='bottom',
        anchor='start',
        font = 'Times New Roman',
        fontWeight='normal',
        fontStyle = "italic",
        fontSize=15)
)

final

alt.ConcatChart(...)

In [257]:
# Save as an HTML file
final.save('final.html')

# Save as a JSON file
final.save('final.json')

In [258]:
# How much do you spend on beverages each week?

# Data Source
alt.data_transformers.disable_max_rows()
source = beverages[beverages[['l_consumption_purchased']].notnull().all(1)] #change variable

col1 = source['l_consumption_purchased'] #!= NaN #change variable
col2 = source['cs_aggr_tier'] != 'NaN'

source = source[conjunction(col1,col2)]
df = source[['hh_id','cs_aggr_tier','l_consumption_purchased', 'locality', 'c182', 'i19a','stove']] #change variable

# Percentage of responses shown in the chart
pct_responses = round(len(pd.unique(df[df[['l_consumption_purchased']].notnull().all(1)]['hh_id'])) /
            3668 *100, 2) #change dataframe variable name

# Draw the Chart
final = alt.Chart(df).transform_joinaggregate(
    total='count(*)'
).transform_calculate(
    pct='1 / datum.total'
).mark_bar().encode(
    alt.X("l_consumption_purchased:Q", #change variable
          bin=alt.Bin(extent=[0, 8000], step=500), # Change the step to adjust bin size
          scale = alt.Scale(domain=(0,8000),clamp = True), # Change the axes limits
         axis = alt.Axis(title = "Nigerian Naira")),
    alt.Y('sum(pct):Q', axis=alt.Axis(format='%'), title = ""),
    tooltip = [alt.Tooltip('l_consumption_purchased:N', title = "Response (Binned)"),  #change variable
               alt.Tooltip('sum(pct):Q', format = '.2%', title = "Percentage")]
).transform_bin(
    "mbin",
    field="m",
    bin=alt.Bin(maxbins=20) # Specify the maximum number of bins
).add_selection(
    stove_select
).transform_filter(
    stove_select
).add_selection(
    primary_fuel_select
).transform_filter(
    primary_fuel_select
).add_selection(
    elec_source_select
).transform_filter(
    elec_source_select 
).add_selection(
    locality_select
).transform_filter(
    locality_select
).add_selection(
    cooking_tier_select
).transform_filter(
    cooking_tier_select 
).properties(
    height = 400,
    width = 500,
    title={
      "text": ["Beverages Expenditures per Week"], 
 #     "subtitle": ["You are viewing {}% of responses from the Nigeria Multi-Tiered Framework Survey.".format(pct_responses), " "],
      "color": "black",
      "subtitleColor": "black", "offset":40
    }
)

final = alt.concat(final,
    title=alt.TitleParams(
        ['', '',  
         'This chart includes responses from {}% of households in the Nigeria MTF survey sample (total size = 3,668).'.format(
             pct_responses),
         'Blank charts indicate that no data matches dropdown filter selection(s).', ''],
        baseline='bottom',
        orient='bottom',
        anchor='start',
        font = 'Times New Roman',
        fontWeight='normal',
        fontStyle = "italic",
        fontSize=15)
)

final

alt.ConcatChart(...)

In [259]:
# Save as an HTML file
final.save('final.html')

# Save as a JSON file
final.save('final.json')

In [226]:
alcohol_tobacco['l_consumption_purchased'].describe()

count     171.000000
mean      709.052632
std       949.183955
min         0.000000
25%       200.000000
50%       400.000000
75%       800.000000
max      5000.000000
Name: l_consumption_purchased, dtype: float64

In [260]:
# How much do you spend on tobacco/alcohol each week?

# Data Source
alt.data_transformers.disable_max_rows()
source = alcohol_tobacco[alcohol_tobacco[['l_consumption_purchased']].notnull().all(1)] #change variable

col1 = source['l_consumption_purchased'] #!= NaN #change variable
col2 = source['cs_aggr_tier'] != 'NaN'

source = source[conjunction(col1,col2)]
df = source[['hh_id','cs_aggr_tier','l_consumption_purchased', 'locality', 'c182', 'i19a','stove']] #change variable

# Percentage of responses shown in the chart
pct_responses = round(len(pd.unique(df[df[['l_consumption_purchased']].notnull().all(1)]['hh_id'])) /
            3668 *100, 2) #change dataframe variable name

# Draw the Chart
final = alt.Chart(df).transform_joinaggregate(
    total='count(*)'
).transform_calculate(
    pct='1 / datum.total'
).mark_bar().encode(
    alt.X("l_consumption_purchased:Q", #change variable
          bin=alt.Bin(extent=[0, 5500], step=250), # Change the step to adjust bin size
          scale = alt.Scale(domain=(0,5500),clamp = True), # Change the axes limits
         axis = alt.Axis(title = "Nigerian Naira")),
    alt.Y('sum(pct):Q', axis=alt.Axis(format='%'), title = ""),
    tooltip = [alt.Tooltip('l_consumption_purchased:N', title = "Response (Binned)"),  #change variable
               alt.Tooltip('sum(pct):Q', format = '.2%', title = "Percentage")]
).transform_bin(
    "mbin",
    field="m",
    bin=alt.Bin(maxbins=20) # Specify the maximum number of bins
).add_selection(
    stove_select
).transform_filter(
    stove_select
).add_selection(
    primary_fuel_select
).transform_filter(
    primary_fuel_select
).add_selection(
    elec_source_select
).transform_filter(
    elec_source_select 
).add_selection(
    locality_select
).transform_filter(
    locality_select
).add_selection(
    cooking_tier_select
).transform_filter(
    cooking_tier_select 
).properties(
    height = 400,
    width = 500,
    title={
      "text": ["Alcohol, Tobacco, & Cigarettes Expenditures per Week"], 
 #     "subtitle": ["You are viewing {}% of responses from the Nigeria Multi-Tiered Framework Survey.".format(pct_responses), " "],
      "color": "black",
      "subtitleColor": "black", "offset":40
    }
)

final = alt.concat(final,
    title=alt.TitleParams(
        ['', '',  
         'This chart includes responses from {}% of households in the Nigeria MTF survey sample (total size = 3,668).'.format(
             pct_responses),
         'Blank charts indicate that no data matches dropdown filter selection(s).', ''],
        baseline='bottom',
        orient='bottom',
        anchor='start',
        font = 'Times New Roman',
        fontWeight='normal',
        fontStyle = "italic",
        fontSize=15)
)

final

alt.ConcatChart(...)

In [261]:
# Save as an HTML file
final.save('final.html')

# Save as a JSON file
final.save('final.json')

#### Templates

In [ ]:
# Bar Chart Example
# B.14 from the Kenya MTF: What is your household’s main source of drinking water?

# Data source
alt.data_transformers.disable_max_rows()
source = module[module[['b_b_14']].notnull().all(1)] # Change your variables here

col1 = source['elc_aggr_tier'] != NaN
col2 = source['b_b_14'] != 'NaN' # Change variables here

source = source[conjunction(col1,col2)]
df = source[['elc_aggr_tier', 'locality_ur', 'b_b_14']] # Change variables here

# Draw the chart 
chart = alt.Chart(df).transform_joinaggregate(
    total = 'count(*)'
).transform_calculate(
    pct = '1 / datum.total'
).encode(
    x = alt.X('b_b_14', # Change variable
              sort=alt.EncodingSortField(field="b_b_14", # Change variable 
                                         op="count", 
                                         order='descending'),
              axis = alt.Axis(title = " ")),
    y = alt.Y('sum(pct):Q', axis = alt.Axis(title = '', format = '%')),
    tooltip = 'b_b_14' # Change variable
).properties(
    height = 400,
    width = 500
)

# Locality Filter
locality_options = [None, 'Urban', 'Rural']
locality_labels = ['National', 'Urban', 'Rural']

locality_dropdown=alt.binding_select(
    options= locality_options, 
    labels = locality_labels, 
    name = "Locality Breakdown  ")
locality_select=alt.selection_single(
    fields=['locality_ur'],
    bind=locality_dropdown)

# Tier Filter
tiers = [None, 'Tier 0', 'Tier 1', 'Tier 2', 'Tier 3', 'Tier 4', 'Tier 5']
tier_labels = ['All Tiers', 'Tier 0', 'Tier 1', 'Tier 2', 'Tier 3', 'Tier 4', 'Tier 5']
tier_dropdown=alt.binding_select(options=tiers, 
                                 labels = tier_labels, 
                                 name = "Electricity Tiers  ")
tier_select=alt.selection_single(fields=['elc_aggr_tier'],
                                bind=tier_dropdown)

# Percentage of responses shown in the chart
pct = df.shape[0] / module.shape[0]

# Final Chart with bells and whistles
final = (chart.mark_bar(color = '#304ca2') + chart.mark_text( # This blue is from the AIP site.
    align = 'center', 
    baseline='bottom'
).encode(
    text = alt.Text('sum(pct):Q', 
                    format = '.2%'))
).add_selection(
    locality_select
).transform_filter(
    locality_select
).add_selection(
    tier_select
).transform_filter(
    tier_select 
).properties(
    title={
      "text": ["Example Bar Chart (YOUR TITLE HERE)"], 
      "subtitle": ["You are viewing XX% of responses from the Nigeria Multi-Tiered Framework Survey.", " "],
      "color": "black",
      "subtitleColor": "black", "offset":40
    }
)

final

In [ ]:
# Primary vs Secondary Cooking Fuel Sources

# Data
alt.data_transformers.disable_max_rows()
source = cooking[cooking[['i19a', 'primary_stove']].notnull().all(1)]

col1 = source['i19a'] != 'NaN'
col2 = source['elc_aggr_tier'] != 'NaN'

source = source[conjunction(col1,col2)]
df = source[['elc_aggr_tier','i19a', 'primary_stove', 'locality']]

# Configure common options
base = alt.Chart(df).transform_aggregate(
    chart_count='count()',
    groupby=['i19a', 'primary_stove']
).encode(
    alt.X('i19a:O', 
          scale=alt.Scale(paddingInner=0), 
          title = "Primary Cooking Fuel"),
    alt.Y('primary_stove:O', 
          scale=alt.Scale(paddingInner=0), 
          title = "Primary Cooking Stove"),
)

# Configure heatmap
heatmap = base.mark_rect().encode(
    color=alt.Color('chart_count:Q',
        scale=alt.Scale(scheme='blues'),
        legend=None
    )
)

# Configure text
text = base.mark_text(baseline='middle'
).transform_joinaggregate(
    count = 'count(chart_count)',
    groupby = ['i19a', 'primary_stove']
).transform_calculate(
    pct = alt.datum.chart_count / df.shape[0]
).encode(
    text=alt.Text('pct:Q', format = '.2%'),
    color=alt.condition(
        alt.datum.chart_count < 300, # Change the color of the text here
        alt.value('black'),
        alt.value('white')
    )
)

# Locality Filter
locality_options = [None, 0, 1]
locality_labels = ['National', 'Urban', 'Rural']

locality_dropdown=alt.binding_select(
    options= locality_options, 
    labels = locality_labels, 
    name = "Locality Breakdown  ")
locality_select=alt.selection_single(
    fields=['locality'],
    bind=locality_dropdown)

# Tier Filter
tiers = [None, 'Tier 0', 'Tier 1', 'Tier 2', 'Tier 3', 'Tier 4', 'Tier 5']
tier_labels = ['All Tiers', 'Tier 0', 'Tier 1', 'Tier 2', 'Tier 3', 'Tier 4', 'Tier 5']
tier_dropdown=alt.binding_select(options=tiers, labels = tier_labels, name = "Electricity Tiers  ")
tier_select=alt.selection_single(fields=['elc_aggr_tier'],
                                bind=tier_dropdown)

# Roof filter
#roofs = [None, 'Corrugated iron sheet', 'Concrete/Cement', 'Thatch', 'Wood and mud', 'Bamboo/Reed', 
 #        'Plastic canvas', 'Asbestos', 'Bricks']
#roof_labels = ['All roof types', 'Corrugated iron sheet', 'Concrete/Cement', 'Thatch', 'Wood and mud', 'Bamboo/Reed', 
 #        'Plastic canvas', 'Asbestos', 'Bricks']
#roof_dropdown=alt.binding_select(options=roofs, labels = roof_labels, name = "Roofs  ")
#roof_select=alt.selection_single(fields=['b_b_11'],
 #                               bind=roof_dropdown)

# Draw the chart
final = (heatmap + text).properties(
    height = 300,
    width = 800
).add_selection(
    locality_select
).transform_filter(
    locality_select
).add_selection(
    tier_select
).transform_filter(
    tier_select 
# ).add_selection(
#     roof_select
# ).transform_filter(
#     roof_select
).properties(
    title={
      "text": ['Commonly Used Cooking Fuels and Stoves'], 
    #  "subtitle": ["You are viewing XX% of responses from the Kenya Multi-Tiered Framework Survey.", " "],
      "color": "black",
      "subtitleColor": "black", "offset":40
    }
)

final

In [ ]:
# Step 1: create the scatterplot
# How much would you sell your land for?

df = module[module[['n_n_1b', 'n_n_1c', 'n_n_1b_unit']].notnull().all(1)]

# Filters
locality_options = [None, 'Urban', 'Rural']
locality_labels = ['National', 'Urban', 'Rural']
locality_dropdown=alt.binding_select(
    options= locality_options, 
    labels = locality_labels, 
    name = "Locality Breakdown  ")
locality_select=alt.selection_single(
    fields=['locality_ur'],
    bind=locality_dropdown)

tiers = [None, 'Tier 0', 'Tier 1', 'Tier 2', 'Tier 3', 'Tier 4', 'Tier 5']
tier_labels = ['All Tiers', 'Tier 0', 'Tier 1', 'Tier 2', 'Tier 3', 'Tier 4', 'Tier 5']
tier_dropdown=alt.binding_select(options=tiers, labels = tier_labels, name = "Electricity Tiers  ")
tier_select=alt.selection_single(fields=['elc_aggr_tier'],
                                bind=tier_dropdown)

# You need 2 unit filters to apply to both the scatterplot and histogram.
units = ['Acre', 'sq metres','Other']
unit_labels = ['Acre', 'Square meter','Other']
unit_dropdown=alt.binding_select(options=units, labels = unit_labels, name = "Units  ")
unit_select=alt.selection_single(fields=['n_n_1b_unit:N'],
                                bind=unit_dropdown)

units = [None, 'Acre', 'sq metres','Other']
unit_labels = ['All units', 'Acre', 'Square meter','Other']
unit_dropdown=alt.binding_select(options=units, labels = unit_labels, name = "Units  ")
unit_select=alt.selection_single(fields=['n_n_1b_unit'],
                                 bind=unit_dropdown)
 
# Scatterplot    
points = alt.Chart(df).mark_point().encode(
    x=alt.X('n_n_1b:Q',
           axis = alt.Axis(title = 'What is the total size of the land?'),
           scale = alt.Scale(domain=(1,100),clamp = True)),
    y=alt.Y('n_n_1c:Q',
            axis=alt.Axis(title='How much would you sell your land for?'),
           scale = alt.Scale(domain=(1,70000000),clamp = True)),
    color = alt.Color('n_n_1b_unit:N', legend = alt.Legend(title = "Units"))
)


scatterplot = (points).properties(
    height = 300,
    width = 500
).add_selection(brush)

scatterplot

In [ ]:
# Step 2: add the histogram
df = module[module[['n_n_1b']].notnull().all(1)]

points = alt.Chart(df).mark_point().encode(
    x=alt.X('n_n_1b:Q',
           axis = alt.Axis(title = 'What is the total size of the land?'),
           scale = alt.Scale(domain=(1,100),clamp = True)),
    y=alt.Y('n_n_1c:Q',
            axis=alt.Axis(title='How much would you sell your land for?'),
           scale = alt.Scale(domain=(1,70000000),clamp = True)),
    color = alt.Color('n_n_1b_unit:N', legend = alt.Legend(title = "Units"))
)

scatterplot = (points).properties(
    height = 300,
    width = 500
).add_selection(brush)

chart = alt.Chart(df).mark_bar(
).transform_joinaggregate(
    total='count(*)'
).transform_calculate(
    pct='1 / datum.total'
).encode(
    alt.X("n_n_1b", 
          bin=alt.Bin(extent=[0, 100], step=5), 
          scale = alt.Scale(domain=(0,100),clamp = True),
         axis = alt.Axis(title = "Units of Land")),
    alt.Y('sum(pct):Q', axis=alt.Axis(format='%'), title = "Percent"),
    tooltip = alt.Tooltip('sum(pct):Q', format = '.2%')
).transform_bin(
    "mbin",
    field="m",
    bin=alt.Bin(maxbins=20)
)

# Draw the chart
histogram = chart.properties(
    height = 300,
    width = 500,
    title = ''
).transform_filter(brush)


scatterplot & histogram

In [ ]:
# Finally, add filters

final = (scatterplot & histogram
).add_selection(
    locality_select
).transform_filter(
    locality_select
).add_selection(
    tier_select
).transform_filter(
    tier_select 
).add_selection(
    unit_select
).transform_filter(
    unit_select
).properties(
    title={
      "text": ["Example (YOUR TITLE HERE) "], 
      "subtitle": ["You are viewing XX% of responses from the Kenya Multi-Tiered Framework Survey.", "Drag and drop a box over the scatterplot to filter the histogram, or use the dropdown filters below.", ""],
      "color": "black",
      "subtitleColor": "black", "offset":40
    }
)

final

In [18]:
# Save as an HTML file
final.save('final.html')

# Save as a JSON file
final.save('final.json')